In [1]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# ========== python ==========
import os
from pathlib import Path
from logging import Logger
from typing import List, Dict, Tuple, Optional, Union, Callable, Final, Literal, get_args
from operator import itemgetter, attrgetter
import itertools
from IPython.display import display

from utils.setup import setup_logger, get_device
from const.const_values import PROJECT_DIR

os.chdir(PROJECT_DIR)
logger: Logger = setup_logger(__name__, f'{PROJECT_DIR}/log/jupyter_run.log')
device = get_device(device_name='cpu', logger=logger)

In [2]:
# jupyter
import seaborn as sns
import matplotlib.pyplot as plt
# Machine learning
import numpy as np
import pandas as pd
import h5py
import optuna
# torch
import torch
from torch.nn import CrossEntropyLoss
from torch.utils.data import Dataset
from torch.utils.data.dataloader import DataLoader
from torch.utils.tensorboard.writer import SummaryWriter
# torch ignite
from ignite.engine import Engine
from ignite.handlers import Checkpoint
# My items
from models.datasets.data_helper import MyDataHelper, MyDataLoaderHelper, DefaultTokens
from models.datasets.datasets_for_story import StoryTriple
# My utils
from utils.setup import load_param
from utils.torch import load_model, torch_fix_seed
# main function
from run_for_KGC import main_function

In [3]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 100)

In [4]:
from const.const_values import CPU, MODEL
from models.KGModel.kg_model import HEAD, RELATION, TAIL
from utils.torch_ignite import TRAINER, EVALUATOR
from const.const_values import DATASETS, DATA_HELPER, DATA_LOADERS, TRAIN_RETURNS

In [5]:
SEED: Final[int] = 42
args_path = f'{PROJECT_DIR}/models/230205/01/param.pkl'
model_path = f'{PROJECT_DIR}/models/230205/01/model.pth'

In [6]:
args = load_param(args_path)

# args.pre_train = True
args.logger = logger
args.device = device
args.batch_size = 16
args.pre_train=False
args.init_embedding_using_bert = False
args.model_path = model_path
args.only_load_trainer_evaluator = True

del args.optuna_file, args.device_name, args.pid, args.study_name, args.n_trials

In [7]:
args

Namespace(notebook=False, console_level='info', logfile='models/230205/01/log.log', param_file='models/230205/01/param.pkl', train_anyway=True, old_data=0, tensorboard_dir='models/230205/01/tensorboard', checkpoint_dir='models/230205/01/checkpoint/', model_path='/Users/ryoyakaneda/Documents/学校/M1Study/knowledge_graph/models/230205/01/model.pth', resume_from_checkpoint=False, resume_from_last_point=False, only_load_trainer_evaluator=True, resume_checkpoint_path=None, pre_train=False, train_valid_test=True, only_train=False, use_for_challenge100=False, use_for_challenge090=False, use_for_challenge075=False, use_title=None, do_optuna=False, story_special_num=5, relation_special_num=5, entity_special_num=5, padding_token_e=0, cls_token_e=1, mask_token_e=2, sep_token_e=3, bos_token_e=4, padding_token_r=0, cls_token_r=1, mask_token_r=2, sep_token_r=3, bos_token_r=4, padding_token_s=0, cls_token_s=1, mask_token_s=2, sep_token_s=3, bos_token_s=4, model_version='03', embedding_dim=128, entity_e

In [8]:
"embedding_dim={}, entity_embedding_dim={}, relation_embedding_dim={}, nhead={}, num_layers={}, ".format(
    args.embedding_dim, args.entity_embedding_dim, args.relation_embedding_dim, args.nhead, args.num_layers,)

'embedding_dim=128, entity_embedding_dim=768, relation_embedding_dim=64, nhead=4, num_layers=4, '

In [9]:
torch_fix_seed(seed=SEED)
return_dict = main_function(args, logger=logger)

2023-02-05 14:51:57 - INFO - run_for_KGC.py - 901 - ----- make datahelper start. -----
2023-02-05 14:51:57 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-05 14:51:57 - INFO - data_helper.py - 334 - entity num: 7812
2023-02-05 14:51:57 - INFO - data_helper.py - 335 - relation num: 62
2023-02-05 14:51:57 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-05 14:51:57 - INFO - data_helper.py - 607 - ========== Show DataHelper ==========
2023-02-05 14:51:57 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-05 14:51:57 - INFO - data_helper.py - 334 - entity num: 7812
2023-02-05 14:51:57 - INFO - data_helper.py - 335 - relation num: 62
2023-02-05 14:51:57 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-05 14:51:57 - INFO - data_helper.py - 609 - entity_special_dicts: {0: '<pad_e>', 1: '<cls_e>', 2: '<mask_e>', 3: '<sep_e>', 4: '<bos_e>'}
2023-02-05 14:51:57 - INFO - data_helper.py - 610 - relation_special_dicts: {

In [10]:
model = return_dict[MODEL]

dataset_train: StoryTriple = return_dict[DATASETS][0]
triple: torch.Tensor = dataset_train.triple
data_helper: MyDataHelper = return_dict[DATA_HELPER]
evaluator: Checkpoint = return_dict[TRAIN_RETURNS][EVALUATOR]

load_model(model, args.model_path, device)
model.eval()

entities, relations = data_helper.processed_entities, data_helper.processed_relations
d_e, d_r = {e: i for i, e in enumerate(entities)}, {r: i for i, r in enumerate(relations)}

triple_df = pd.DataFrame([(entities[_t[0]], relations[_t[1]], entities[_t[2]]) for _t in triple], columns=[HEAD, RELATION, TAIL])
story_entities = triple_df[HEAD].tolist()

In [11]:
with torch.no_grad():
    model.eval()
    valid = return_dict['data_loaders'].valid_dataloader
    evaluator = return_dict['train_returns']['evaluator']
    evaluator.run(valid)
    display(evaluator)

[1/101]   1%|           [00:00<?]

In [29]:
evaluator.state.metrics

{'loss': 10.193101089779693,
 'story_loss': 1.7494380704247126,
 'relation_loss': 1.591783373662741,
 'entity_loss': 6.851879634479485,
 'story_accuracy': 0.5847662822670004,
 'relation_accuracy': 0.5304168205633302,
 'entity_accuracy': 0.18752137453660003}

### One of the inputs is shown as an example.

### The sequence contains triples from the beginning of each scene to the specified length. In this case, the length is set to 512.

In [12]:
most_frequency_percent_list = []
num_list = []

for tensor in dataset_train:
    head_unique, head_unique_count = torch.unique(tensor[:, 0], return_counts=True)
    relation_unique, relation_unique_count = torch.unique(tensor[:, 1], return_counts=True)
    tail_unique, tail_unique_count = torch.unique(tensor[:, 2], return_counts=True)
    entity_unique, entity_unique_count = torch.unique(tensor[:, (0,2)], return_counts=True)

    head_unique, head_unique_count = [_tensor[head_unique!=4] for _tensor in (head_unique, head_unique_count)]
    relation_unique, relation_unique_count = [_tensor[relation_unique!=4] for _tensor in (relation_unique, relation_unique_count)]
    tail_unique, tail_unique_count = [_tensor[tail_unique!=4] for _tensor in (tail_unique, tail_unique_count)]
    entity_unique, entity_unique_count =  [_tensor[entity_unique!=4] for _tensor in (entity_unique, entity_unique_count)]

    head_most_frequency = torch.max(head_unique_count)
    relation_most_frequency = torch.max(relation_unique_count)
    tail_most_frequency = torch.max(tail_unique_count)
    entity_most_frequency = torch.max(entity_unique_count)

    print(entities[tail_unique[torch.argmax(tail_unique_count)]])
    most_frequency_percent_list.append(
        [(value/len(tensor)).item() for value in (head_most_frequency, relation_most_frequency, tail_most_frequency, entity_most_frequency) ])
    num_list.append([1/len(value) for value in (head_unique, relation_unique, tail_unique, entity_unique)])

torch.tensor(most_frequency_percent_list).mean(dim=0), torch.tensor(num_list).mean(dim=0)

AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrange:Lady_Brackenstall
AbbeyGrang

(tensor([0.0429, 0.2160, 0.0969, 0.1016]),
 tensor([0.0102, 0.0824, 0.0059, 0.0042]))

In [13]:
print("training sequence shape:", dataset_train[0].shape)
dataset_train[0]

training sequence shape: torch.Size([512, 3])


tensor([[   4,    4,    4],
        [3958,   45,    6],
        [3958,   26,    6],
        ...,
        [4067,   33,  400],
        [   4,    4,    4],
        [4068,    6,  430]])

#### Note that the data presented in the previous section are part of this series below.

In [14]:
triple_df[triple_df['head'].str.contains('ResidentPatient')]

head          relation                           tail
9349    ResidentPatient:001       kgc:subject                AllTitle:Holmes
9350    ResidentPatient:001  kgc:hasPredicate           word.predicate:guess
9351    ResidentPatient:001          kgc:what            ResidentPatient:002
9352    ResidentPatient:001          kgc:what            ResidentPatient:004
9353    ResidentPatient:001          kgc:when  ResidentPatient:1889-10-20T22
...                     ...               ...                            ...
10794   ResidentPatient:324   kgc:hasProperty            word.predicate:want
10795   ResidentPatient:324          kgc:what           ResidentPatient:324a
10797  ResidentPatient:324a       kgc:subject    ResidentPatient:Blessington
10798  ResidentPatient:324a   kgc:hasProperty            word.predicate:hide
10799  ResidentPatient:324a          kgc:what   ResidentPatient:Own_identity

[1110 rows x 3 columns]

This is the model made by Pytorch.

In [15]:
model

KgStoryTransformer03(
  (entity_embeddings): Embedding(7817, 768, padding_idx=0)
  (relation_embeddings): Embedding(67, 64, padding_idx=0)
  (pe): PositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=1028, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=1028, out_features=128, bias=True)
        (norm1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
        (activation): GELU(approximate='none')
      )
      (1): TransformerEncoderLayer(
      

This function is used to visualize Attention. The description is skipped.

In [16]:
# This is sub functions for getting Attention.
def extract(_model, target, inputs):
    """This is sub functions for getting Attention.

    """
    features = None

    def forward_hook(_module, _inputs, _):
        nonlocal features
        x, _, _ = _inputs
        outputs = _module.forward(x, x, x, need_weights=True)[1]
        features = outputs.detach().clone()

    handle = target.register_forward_hook(forward_hook)

    _model.eval()
    _model(inputs, torch.LongTensor([[]]), torch.LongTensor([[]]), torch.LongTensor([[]]))

    handle.remove()

    return features

# This is main functions for getting Attention.
def get_attention(input_):
    """This is main functions for getting Attention.

    """
    assert len(input_) == 1
    features = extract(model, model.transformer.layers[-1].self_attn, input_)[0]
    df_attention = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_[0])])
    df_attention.columns=[HEAD, RELATION, TAIL] + [f'atten_from{i}' for i in range(len(df_attention.columns)-3)]
    return df_attention

def show_attention_heatmap(df_attention):
    sns.heatmap(df_attention.iloc[:,3:])
    plt.show()

In [17]:
MASK_E = DefaultTokens.MASK_E
KILL = 'word.predicate:kill'

TAKE = 'word.predicate:take'
BRING = 'word.predicate:bring'
DIE = 'word.predicate:die'
HIDE = 'word.predicate:hide'

The input to the model is the following function's "question_".
There are some last scenes and criminal scene after last scene.
Each part of criminal scene are changed into a victim or <mask>, and the MASK part is estimated.

In [18]:
bos_triple = [d_e[DefaultTokens.BOS_E], d_r[DefaultTokens.BOS_R],d_e[DefaultTokens.BOS_E]]
mask_e_id = d_e[DefaultTokens.MASK_E]
Holmes_id =d_e['AllTitle:Holmes']

def make_ranking(from_story_name, to_story_name, predicate_, whom_, subject_, why_, what_, where_):
    if not (from_story_name is None and to_story_name is None):
        _start_index = story_entities.index(from_story_name)-1
        _end_index = len(story_entities) - story_entities[::-1].index(to_story_name)
    else:
        _start_index = 0
        _end_index = 0
    question_ = torch.tensor(
        [
            # [... last 80 scenes ...],
            # ...
            bos_triple,
            [mask_e_id, d_r['kgc:infoSource'],     Holmes_id      ],
            [mask_e_id, d_r['kgc:hasPredicate'],   d_e[predicate_]],
            [mask_e_id, d_r['kgc:whom'],           d_e[whom_     ]],
            [mask_e_id, d_r['kgc:subject'],        d_e[subject_  ]],
            [mask_e_id, d_r['kgc:why'],            d_e[why_      ]],
            [mask_e_id, d_r['kgc:what'],           d_e[what_     ]],
            [mask_e_id, d_r['kgc:where'],          d_e[where_    ]],
        ]
    )
    mask_ = torch.zeros_like(question_, dtype=torch.bool) # not mask all position
    mask_[1:, 0] = True                                   # where head position without bos token
    mask_[1:, 2] = True                                   # where tail position without bos token

    last_triples = triple[_start_index: _end_index]

    questions = torch.cat([last_triples, question_], dim=0).unsqueeze(0)
    masks = torch.cat([torch.zeros_like(last_triples), mask_], dim=0).to(torch.bool).transpose(1,0).unsqueeze(0)

    data_list = []
    with torch.no_grad():
        _, (story_pred, relation_pred, entity_pred) = model(questions, masks[:,0], masks[:,1], masks[:,2])
        sorted_ = torch.argsort(entity_pred, dim=1, descending=True)
        for i in range(sorted_.shape[1]):
            ans_= sorted_[:, i]
            info_source_, predicate_pred, whom_pred, subject_pred, why_pred, what_pred, where_pred = ans_
            data_list.append([entities[predicate_pred], entities[whom_pred], entities[subject_pred], entities[why_pred], entities[what_pred], entities[where_pred]])
    df_ranking = pd.DataFrame(data_list, columns=['predicate', 'whom', 'subject', 'why', 'what', 'where'])
    df_attension = get_attention(questions)

    return df_ranking, df_attension

In [19]:
def main_func01(_title, _victim_name, criminal, predicate, _last_index, _story_len):
    from_ = f'{_title}:{_last_index-_story_len+1}'
    to_ = f'{_title}:{_last_index}'
    predicate = predicate
    victim = f'{_title}:{_victim_name}'
    criminal = f'{_title}:{criminal}'
    df_ranking, df_attention = make_ranking(
        from_, to_, predicate, victim, MASK_E, MASK_E, MASK_E, MASK_E)
    df_ranking.index.name='ranking'

    pred_rank = df_ranking.index[df_ranking['subject']==criminal].tolist()
    pred_rank = pred_rank[0] if len(pred_rank)==1 else -1
    logger.info(f"The pred ranking about {criminal} is {pred_rank}")
    display(df_ranking.iloc[:max(20, pred_rank)])
    len_ = len(df_attention)
    for i in range(len_-10, len_):
        print(f"index={i}, triple={df_attention.iloc[i,:3].tolist()}, attention list")
        display(df_attention.sort_values(f'atten_from{i}', ascending=False).iloc[:,[0,1,2,3+i]],)
    return df_ranking, df_attention

def check_killer(_title, _victim_name, _killer_name, _last_index, _story_len):
    return main_func01(_title, _victim_name, _killer_name, KILL, _last_index, _story_len)

# Estimate Criminals

### SpeckledBand(まだらの紐)
Who killed Julia? (criminal & explanation)
被害者: Julia
犯人: Roylott
犯行に用いたもの: snake
犯行動機: 母の相続財産を独占したい

### Input sequence is like this.


|     head     | relation  |            tail            |
|:------------:|:---------:|:--------------------------:|
| SpeckledBand |  stories  |            ...             |
|     ...      |    ...    |            ...             |
|    \<bos>    |  \<bos>   |           \<bos>           |
|  \<unknown>  | predicate |            kill            |
|  \<unknown>  |   whom    |           Julia            |
|  \<unknown>  |  subject  | \<mask(Answer is Roylott)> |
|  \<unknown>  |    why    |          \<mask>           |
|  \<unknown>  |   what    |          \<mask>           |
|  \<unknown>  |    why    |          \<mask>           |

In [20]:
def do_SpeckledBand_pred():
    title = 'SpeckledBand'
    victim_name = 'Julia'
    killer_name = 'Roylott'
    last_index = 401
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention
do_SpeckledBand_pred()
pass

2023-02-05 14:56:45 - INFO - 3560443472.py - 13 - The pred ranking about SpeckledBand:Roylott is 0


predicate  \
ranking                                     
0                     word.predicate:kill   
1                   word.predicate:return   
2                     DevilsFoot:Roundhay   
3            DateTime:1883-04-01T15:00:00   
4                  SilverBlaze:Ned_Hunter   
5                       word.predicate:go   
6                    word.predicate:shoot   
7                     word.predicate:drop   
8                     word.predicate:find   
9                                 <bos_e>   
10                     word.predicate:hit   
11                   word.predicate:think   
12                 word.predicate:examine   
13           SpeckledBand:Julia_s_bedroom   
14             SpeckledBand:1883-03-31T23   
15       SilverBlaze:Wife_of_John_Straker   
16                       CrookedMan:Henry   
17          AbbeyGrange:Lady_Brackenstall   
18           DateTime:1883-04-01T10:00:00   
19            DancingMen:1898-08-13T03:02   

                                                     whom  \
ranking                                                     
0                                     DevilsFoot:Roundhay   
1                               DevilsFoot:Doctor_Richard   
2                                         AllTitle:Watson   
3                                        CrookedMan:Henry   
4                                     word.predicate:drop   
5                                       CrookedMan:police   
6                           AbbeyGrange:Lady_Brackenstall   
7                              ACaseOfIdentity:Sutherland   
8                                    SpeckledBand:Roylott   
9                                       DevilsFoot:window   
10                                                <bos_e>   
11       ResidentPatient:Several_thousand_investment_gold   
12                                  word.predicate:return   
13                                        DevilsFoot:Owen   
14                                      word.predicate:go   
15                       SilverBlaze:Wife_of_John_Straker   
16                                AbbeyGrange:Jack_Croker   
17                  AbbeyGrange:Burglary_team_of_Lewisham   
18                                   word.predicate:think   
19                               SilverBlaze:John_Straker   

                                                  subject  \
ranking                                                     
0                                    SpeckledBand:Roylott   
1                                                 <bos_e>   
2                                 AbbeyGrange:Jack_Croker   
3                             ResidentPatient:Blessington   
4                               DevilsFoot:Doctor_Richard   
5                                     DevilsFoot:Roundhay   
6                                      SpeckledBand:Helen   
7                                SilverBlaze:John_Straker   
8                            SpeckledBand:VentilationHole   
9                                         AllTitle:Watson   
10                       SilverBlaze:Wife_of_John_Straker   
11                                 SilverBlaze:Ned_Hunter   
12                                      word.predicate:go   
13                                word.predicate:approach   
14                                    word.predicate:know   
15                               CrookedMan:Royal_Mallows   
16                          AbbeyGrange:Thought_of_Holmes   
17                                   word.predicate:carry   
18                                  word.predicate:happen   
19       ResidentPatient:Several_thousand_investment_gold   

                                                      why  \
ranking                                                     
0                                                 <bos_e>   
1                                        CrookedMan:Nancy   
2                                     DevilsFoot:Roundhay   
3                                     word.predica

index=380, triple=['SpeckledBand:401', 'kgc:subject', 'SpeckledBand:Roma'], attention list


head          relation  \
342  SpeckledBand:393          kgc:what   
338  SpeckledBand:392          kgc:what   
119  SpeckledBand:346   kgc:hasProperty   
343  SpeckledBand:393          kgc:when   
167  SpeckledBand:356          kgc:what   
163  SpeckledBand:355          kgc:time   
169  SpeckledBand:356          kgc:time   
121  SpeckledBand:346          kgc:time   
347  SpeckledBand:394          kgc:what   
174           <bos_e>           <bos_r>   
357  SpeckledBand:396          kgc:time   
148           <bos_e>           <bos_r>   
116  SpeckledBand:345          kgc:time   
111  SpeckledBand:344          kgc:time   
362  SpeckledBand:397          kgc:time   
164           <bos_e>           <bos_r>   
153           <bos_e>           <bos_r>   
360  SpeckledBand:397   kgc:hasProperty   
130  SpeckledBand:348          kgc:what   
127  SpeckledBand:347          kgc:time   
132  SpeckledBand:348          kgc:time   
179           <bos_e>           <bos_r>   
138           <bos_e>           <bos_r>   
319           <bos_e>           <bos_r>   
327           <bos_e>           <bos_r>   
317  SpeckledBand:387          kgc:what   
314           <bos_e>           <bos_r>   
170           <bos_e>           <bos_r>   
323           <bos_e>           <bos_r>   
112           <bos_e>           <bos_r>   
122           <bos_e>           <bos_r>   
109           <bos_e>           <bos_r>   
144           <bos_e>           <bos_r>   
133           <bos_e>           <bos_r>   
311           <bos_e>           <bos_r>   
161           <bos_e>           <bos_r>   
137  SpeckledBand:349          kgc:time   
382           <bos_e>           <bos_r>   
0             <bos_e>           <bos_r>   
301  SpeckledBand:383          kgc:what   
5             <bos_e>           <bos_r>   
291           <bos_e>           <bos_r>   
344           <bos_e>           <bos_r>   
339           <bos_e>           <bos_r>   
117           <bos_e>           <bos_r>   
283           <bos_e>           <bos_r>   
201           <bos_e>           <bos_r>   
248           <bos_e>           <bos_r>   
256           <bos_e>           <bos_r>   
157           <bos_e>           <bos_r>   
47            <bos_e>           <bos_r>   
340  SpeckledBand:393       kgc:subject   
261           <bos_e>           <bos_r>   
198           <bos_e>           <bos_r>   
313  SpeckledBand:386          kgc:what   
307           <bos_e>           <bos_r>   
213           <bos_e>           <bos_r>   
42            <bos_e>           <bos_r>   
363           <bos_e>           <bos_r>   
225           <bos_e>           <bos_r>   
332           <bos_e>           <bos_r>   
231           <bos_e>           <bos_r>   
52            <bos_e>           <bos_r>   
82            <bos_e>           <bos_r>   
300  SpeckledBand:383          kgc:what   
294           <bos_e>           <bos_r>   
128           <bos_e>           <bos_r>   
224  SpeckledBand:367          kgc:time   
296  SpeckledBand:382          kgc:what   
193           <bos_e>           <bos_r>   
379           <bos_e>           <bos_r>   
207           <bos_e>           <bos_r>   
274           <bos_e>           <bos_r>   
36            <bos_e>           <bos_r>   
104           <bos_e>           <bos_r>   
187  SpeckledBand:360          kgc:time   
183  SpeckledBand:359          kgc:time   
358           <bos_e>           <bos_r>   
336           <bos_e>           <bos_r>   
11            <bos_e>           <bos_r>   
184           <bos_e>           <bos_r>   
388          <mask_e>          kgc:what   
219           <bos_e>           <bos_r>   
156  SpeckledBand:353          kgc:time   
303  SpeckledBand:383          kgc:what   
279           <bos_e>           <bos_r>   
289           <bos_e>           <bos_r>   
188           <bos_e>           <bos_r>   
268           <bos_e>           <bos_r>   
253           <bos_e>           <bos_r>   
297           <bos_e>           <bos_r>   
374           <bos_e>           <bos_r>   
369           <bos

index=381, triple=['SpeckledBand:401', 'kgc:hasProperty', 'word.predicate:band'], attention list


...

head          relation  \
348  SpeckledBand:394          kgc:when   
350  SpeckledBand:395          kgc:what   
131  SpeckledBand:348          kgc:when   
380  SpeckledBand:401       kgc:subject   
118  SpeckledBand:346       kgc:subject   
130  SpeckledBand:348          kgc:what   
168  SpeckledBand:356          kgc:when   
345  SpeckledBand:394       kgc:subject   
71   SpeckledBand:335   kgc:hasProperty   
60   SpeckledBand:333          kgc:what   
102  SpeckledBand:341          kgc:when   
72   SpeckledBand:335   kgc:hasProperty   
136  SpeckledBand:349          kgc:when   
120  SpeckledBand:346          kgc:when   
359  SpeckledBand:397       kgc:subject   
191  SpeckledBand:361          kgc:when   
85   SpeckledBand:338    kgc:infoSource   
69   SpeckledBand:335       kgc:subject   
351  SpeckledBand:395          kgc:when   
108  SpeckledBand:343          kgc:when   
361  SpeckledBand:397          kgc:when   
173  SpeckledBand:357          kgc:when   
347  SpeckledBand:394          kgc:what   
160  SpeckledBand:354          kgc:when   
115  SpeckledBand:345          kgc:when   
92   SpeckledBand:339          kgc:when   
61   SpeckledBand:333          kgc:when   
70   SpeckledBand:335   kgc:hasProperty   
167  SpeckledBand:356          kgc:what   
81   SpeckledBand:337          kgc:when   
226  SpeckledBand:368       kgc:subject   
66   SpeckledBand:334          kgc:when   
182  SpeckledBand:359          kgc:when   
90   SpeckledBand:339   kgc:hasProperty   
89   SpeckledBand:339       kgc:subject   
147  SpeckledBand:351          kgc:when   
178  SpeckledBand:358          kgc:when   
96   SpeckledBand:340          kgc:when   
91   SpeckledBand:339    kgc:infoSource   
343  SpeckledBand:393          kgc:when   
142  SpeckledBand:350          kgc:when   
257  SpeckledBand:374       kgc:subject   
126  SpeckledBand:347          kgc:when   
292  SpeckledBand:381       kgc:subject   
171  SpeckledBand:357       kgc:subject   
145  SpeckledBand:351       kgc:subject   
31   SpeckledBand:327          kgc:what   
149  SpeckledBand:352       kgc:subject   
65   SpeckledBand:334   kgc:hasProperty   
265  SpeckledBand:375    kgc:infoSource   
150  SpeckledBand:352          kgc:what   
64   SpeckledBand:334       kgc:subject   
77   SpeckledBand:336          kgc:when   
159  SpeckledBand:354          kgc:what   
165  SpeckledBand:356       kgc:subject   
139  SpeckledBand:350       kgc:subject   
59   SpeckledBand:333  kgc:hasPredicate   
196  SpeckledBand:362          kgc:when   
210  SpeckledBand:365    kgc:infoSource   
86   SpeckledBand:338          kgc:when   
356  SpeckledBand:396          kgc:when   
271  SpeckledBand:376    kgc:infoSource   
235  SpeckledBand:369          kgc:when   
155  SpeckledBand:353          kgc:when   
43   SpeckledBand:330       kgc:subject   
364  SpeckledBand:398       kgc:subject   
134  SpeckledBand:349       kgc:subject   
216  SpeckledBand:366          kgc:what   
83   SpeckledBand:338       kgc:subject   
53   SpeckledBand:332       kgc:subject   
152  SpeckledBand:352          kgc:when   
199  SpeckledBand:363       kgc:subject   
189  SpeckledBand:361       kgc:subject   
123  SpeckledBand:347       kgc:subject   
362  SpeckledBand:397          kgc:time   
234  SpeckledBand:369          kgc:what   
204  SpeckledBand:364    kgc:infoSource   
146  SpeckledBand:351   kgc:hasProperty   
80   SpeckledBand:337       kgc:subject   
169  SpeckledBand:356          kgc:time   
367  SpeckledBand:398          kgc:when   
194  SpeckledBand:362       kgc:subject   
205  SpeckledBand:364          kgc:when   
354  SpeckledBand:396       kgc:subject   
180  SpeckledBand:359       kgc:subject   
172  SpeckledBand:357   kgc:hasProperty   
223  SpeckledBand:367          kgc:when   
360  SpeckledBand:397   kgc:hasProperty   
170           <bos_e>           <bos_r>   
222  SpeckledBand:367          kgc:what   
68            <bos_e>           <bos_r>   
333  SpeckledBand:391          kgc:what   
73            <bos

index=388, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
345  SpeckledBand:394       kgc:subject   
118  SpeckledBand:346       kgc:subject   
380  SpeckledBand:401       kgc:subject   
165  SpeckledBand:356       kgc:subject   
340  SpeckledBand:393       kgc:subject   
226  SpeckledBand:368       kgc:subject   
280  SpeckledBand:378       kgc:subject   
328  SpeckledBand:390       kgc:subject   
139  SpeckledBand:350       kgc:subject   
171  SpeckledBand:357       kgc:subject   
292  SpeckledBand:381       kgc:subject   
329  SpeckledBand:390       kgc:subject   
134  SpeckledBand:349       kgc:subject   
315  SpeckledBand:387       kgc:subject   
123  SpeckledBand:347       kgc:subject   
298  SpeckledBand:383       kgc:subject   
130  SpeckledBand:348          kgc:what   
284  SpeckledBand:379       kgc:subject   
162  SpeckledBand:355       kgc:subject   
110  SpeckledBand:344       kgc:subject   
64   SpeckledBand:334       kgc:subject   
69   SpeckledBand:335       kgc:subject   
175  SpeckledBand:358       kgc:subject   
359  SpeckledBand:397       kgc:subject   
257  SpeckledBand:374       kgc:subject   
145  SpeckledBand:351       kgc:subject   
347  SpeckledBand:394          kgc:what   
337  SpeckledBand:392       kgc:subject   
149  SpeckledBand:352       kgc:subject   
338  SpeckledBand:392          kgc:what   
120  SpeckledBand:346          kgc:when   
320  SpeckledBand:388       kgc:subject   
89   SpeckledBand:339       kgc:subject   
83   SpeckledBand:338       kgc:subject   
105  SpeckledBand:343       kgc:subject   
342  SpeckledBand:393          kgc:what   
364  SpeckledBand:398       kgc:subject   
210  SpeckledBand:365    kgc:infoSource   
113  SpeckledBand:345       kgc:subject   
102  SpeckledBand:341          kgc:when   
119  SpeckledBand:346   kgc:hasProperty   
115  SpeckledBand:345          kgc:when   
168  SpeckledBand:356          kgc:when   
232  SpeckledBand:369       kgc:subject   
85   SpeckledBand:338    kgc:infoSource   
121  SpeckledBand:346          kgc:time   
132  SpeckledBand:348          kgc:time   
167  SpeckledBand:356          kgc:what   
333  SpeckledBand:391          kgc:what   
388          <mask_e>          kgc:what   
360  SpeckledBand:397   kgc:hasProperty   
361  SpeckledBand:397          kgc:when   
317  SpeckledBand:387          kgc:what   
31   SpeckledBand:327          kgc:what   
127  SpeckledBand:347          kgc:time   
191  SpeckledBand:361          kgc:when   
169  SpeckledBand:356          kgc:time   
159  SpeckledBand:354          kgc:what   
116  SpeckledBand:345          kgc:time   
131  SpeckledBand:348          kgc:when   
163  SpeckledBand:355          kgc:time   
367  SpeckledBand:398          kgc:when   
126  SpeckledBand:347          kgc:when   
313  SpeckledBand:386          kgc:what   
362  SpeckledBand:397          kgc:time   
111  SpeckledBand:344          kgc:time   
222  SpeckledBand:367          kgc:what   
243  SpeckledBand:371       kgc:subject   
183  SpeckledBand:359          kgc:time   
354  SpeckledBand:396       kgc:subject   
185  SpeckledBand:360       kgc:subject   
137  SpeckledBand:349          kgc:time   
93   SpeckledBand:339          kgc:time   
160  SpeckledBand:354          kgc:when   
318  SpeckledBand:387          kgc:whom   
136  SpeckledBand:349          kgc:when   
363           <bos_e>           <bos_r>   
133           <bos_e>           <bos_r>   
358           <bos_e>           <bos_r>   
182  SpeckledBand:359          kgc:when   
220  SpeckledBand:367       kgc:subject   
103  SpeckledBand:341          kgc:time   
369           <bos_e>           <bos_r>   
187  SpeckledBand:360          kgc:time   
370  SpeckledBand:399       kgc:subject   
374           <bos_e>           <bos_r>   
128           <bos_e>           <bos_r>   
180  SpeckledBand:359       kgc:subject   
164           <bos_e>           <bos_r>   
296  SpeckledBand:382          kgc:what   
108  SpeckledBand:343          kgc:when   
350  SpeckledBand:395          kgc:what   
170           <bos

index=389, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
171  SpeckledBand:357       kgc:subject   
165  SpeckledBand:356       kgc:subject   
168  SpeckledBand:356          kgc:when   
120  SpeckledBand:346          kgc:when   
131  SpeckledBand:348          kgc:when   
102  SpeckledBand:341          kgc:when   
160  SpeckledBand:354          kgc:when   
359  SpeckledBand:397       kgc:subject   
136  SpeckledBand:349          kgc:when   
115  SpeckledBand:345          kgc:when   
60   SpeckledBand:333          kgc:what   
118  SpeckledBand:346       kgc:subject   
191  SpeckledBand:361          kgc:when   
189  SpeckledBand:361       kgc:subject   
364  SpeckledBand:398       kgc:subject   
223  SpeckledBand:367          kgc:when   
61   SpeckledBand:333          kgc:when   
108  SpeckledBand:343          kgc:when   
361  SpeckledBand:397          kgc:when   
173  SpeckledBand:357          kgc:when   
64   SpeckledBand:334       kgc:subject   
43   SpeckledBand:330       kgc:subject   
342  SpeckledBand:393          kgc:what   
343  SpeckledBand:393          kgc:when   
260  SpeckledBand:374          kgc:when   
69   SpeckledBand:335       kgc:subject   
66   SpeckledBand:334          kgc:when   
169  SpeckledBand:356          kgc:time   
308  SpeckledBand:385       kgc:subject   
222  SpeckledBand:367          kgc:what   
147  SpeckledBand:351          kgc:when   
211  SpeckledBand:365          kgc:when   
210  SpeckledBand:365    kgc:infoSource   
348  SpeckledBand:394          kgc:when   
163  SpeckledBand:355          kgc:time   
132  SpeckledBand:348          kgc:time   
92   SpeckledBand:339          kgc:when   
96   SpeckledBand:340          kgc:when   
167  SpeckledBand:356          kgc:what   
152  SpeckledBand:352          kgc:when   
91   SpeckledBand:339    kgc:infoSource   
182  SpeckledBand:359          kgc:when   
155  SpeckledBand:353          kgc:when   
126  SpeckledBand:347          kgc:when   
347  SpeckledBand:394          kgc:what   
196  SpeckledBand:362          kgc:when   
205  SpeckledBand:364          kgc:when   
313  SpeckledBand:386          kgc:what   
318  SpeckledBand:387          kgc:whom   
45   SpeckledBand:330          kgc:when   
178  SpeckledBand:358          kgc:when   
375  SpeckledBand:400       kgc:subject   
142  SpeckledBand:350          kgc:when   
265  SpeckledBand:375    kgc:infoSource   
130  SpeckledBand:348          kgc:what   
271  SpeckledBand:376    kgc:infoSource   
127  SpeckledBand:347          kgc:time   
333  SpeckledBand:391          kgc:what   
370  SpeckledBand:399       kgc:subject   
362  SpeckledBand:397          kgc:time   
357  SpeckledBand:396          kgc:time   
71   SpeckledBand:335   kgc:hasProperty   
85   SpeckledBand:338    kgc:infoSource   
145  SpeckledBand:351       kgc:subject   
367  SpeckledBand:398          kgc:when   
352  SpeckledBand:395          kgc:time   
351  SpeckledBand:395          kgc:when   
121  SpeckledBand:346          kgc:time   
204  SpeckledBand:364    kgc:infoSource   
137  SpeckledBand:349          kgc:time   
338  SpeckledBand:392          kgc:what   
345  SpeckledBand:394       kgc:subject   
199  SpeckledBand:363       kgc:subject   
292  SpeckledBand:381       kgc:subject   
224  SpeckledBand:367          kgc:time   
217  SpeckledBand:366          kgc:when   
229  SpeckledBand:368          kgc:when   
266  SpeckledBand:375          kgc:when   
156  SpeckledBand:353          kgc:time   
81   SpeckledBand:337          kgc:when   
202  SpeckledBand:364       kgc:subject   
110  SpeckledBand:344       kgc:subject   
354  SpeckledBand:396       kgc:subject   
3    SpeckledBand:322          kgc:when   
356  SpeckledBand:396          kgc:when   
383          <mask_e>    kgc:infoSource   
183  SpeckledBand:359          kgc:time   
113  SpeckledBand:345       kgc:subject   
177  SpeckledBand:358          kgc:when   
111  SpeckledBand:344          kgc:time   
116  SpeckledBand:345          kgc:time   
197  SpeckledBand:362          kgc:time   
77   SpeckledBand:

### DevilsFoot(悪魔の足跡１)
Who killed the victims? (criminal & explanation)
被害者: Brenda
犯人: Mortimer
犯行動機: 財産

In [21]:
def do_devil1_pred():
    title = 'DevilsFoot'
    victim_name = 'Brenda'
    killer_name = 'Mortimer'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil1_pred()
pass

2023-02-05 14:56:46 - INFO - 3560443472.py - 13 - The pred ranking about DevilsFoot:Mortimer is 0


predicate                             whom  \
ranking                                                                   
0                  word.predicate:kill                DevilsFoot:Brenda   
1                word.predicate:return              DevilsFoot:Roundhay   
2               word.predicate:examine      ResidentPatient:Elderly_man   
3                 word.predicate:guess              DevilsFoot:Mortimer   
4                  DevilsFoot:Roundhay                  AllTitle:Holmes   
5         DateTime:1883-04-01T15:00:00               word.predicate:say   
6                  word.predicate:find                          <bos_e>   
7                 word.predicate:think                DevilsFoot:window   
8        AbbeyGrange:Lady_Brackenstall       ACaseOfIdentity:Sutherland   
9                ACaseOfIdentity:Woman  ResidentPatient:Percy_Trevelyan   
10                             <bos_e>     DateTime:1883-04-01T14:00:00   
11                 word.predicate:call             word.predicate:think   
12                 word.predicate:lead       ResidentPatient:Helper_boy   
13              SilverBlaze:Ned_Hunter                  DevilsFoot:Owen   
14                    CrookedMan:beast        DevilsFoot:Doctor_Richard   
15                   word.predicate:go         SilverBlaze:John_Straker   
16                     AllTitle:Holmes      ResidentPatient:Blessington   
17                word.predicate:write              DevilsFoot:Criminal   
18                 word.predicate:fall             word.predicate:guess   
19        DateTime:1857-07-09T00:00:00           word.predicate:request   

                                          subject  \
ranking                                             
0                             DevilsFoot:Mortimer   
1                     ResidentPatient:Blessington   
2                                 AllTitle:Holmes   
3                       DevilsFoot:Doctor_Richard   
4                                         <bos_e>   
5                             DevilsFoot:Roundhay   
6                 ResidentPatient:Percy_Trevelyan   
7                        SilverBlaze:Silver_Blaze   
8                                CrookedMan:Henry   
9                      ACaseOfIdentity:Sutherland   
10                    ResidentPatient:Elderly_man   
11                               CrookedMan:beast   
12       ResidentPatient:Worthington_bank_Robbers   
13                      ResidentPatient:Young_man   
14                       SilverBlaze:John_Straker   
15                                DevilsFoot:Owen   
16                        AbbeyGrange:Jack_Croker   
17                            word.predicate:meet   
18                   DateTime:1887-07-06T21:15:00   
19                                AllTitle:Watson   

                                              why  \
ranking                                             
0                                         <bos_e>   
1                             DevilsFoot:Mortimer   
2                             DevilsFoot:Roundhay   
3                          SilverBlaze:Ned_Hunter   
4                        AbbeyGrange:cord_of_bell   
5                     ResidentPatient:Blessington   
6                                CrookedMan:Nancy   
7                        SilverBlaze:Colonel_Ross   
8                        SilverBlaze:John_Straker   
9                            word.predicate:shoot   
10                         word.predicate:notHave   
11       ResidentPatient:Worthington_bank_Robbers   
12                    DancingMen:1898-08-13T03:00   
13                   SpeckledBand:VentilationHole   
14                             word.predicate:sit   
15                       SilverBlaze:Silver_Blaze   
16                      DevilsFoot:Doctor_Richard   
17                           word.predicate:think   
18                        AbbeyGrange:Jack_Croker   
19                            word.predicate:find   

                                            

index=358, triple=['DevilsFoot:489', 'kgc:hasPredicate', 'word.predicate:find'], attention list


head          relation  \
33   DevilsFoot:415         kgc:where   
48   DevilsFoot:418          kgc:time   
143  DevilsFoot:439          kgc:time   
155  DevilsFoot:442          kgc:what   
58   DevilsFoot:420          kgc:when   
218  DevilsFoot:457       kgc:subject   
276  DevilsFoot:471          kgc:what   
275  DevilsFoot:471          kgc:what   
53   DevilsFoot:419           kgc:why   
75   DevilsFoot:423    kgc:infoSource   
240  DevilsFoot:462          kgc:what   
277  DevilsFoot:471          kgc:what   
367        <mask_e>         kgc:where   
365        <mask_e>           kgc:why   
29   DevilsFoot:414    kgc:infoSource   
162  DevilsFoot:444       kgc:subject   
40   DevilsFoot:417          kgc:what   
192  DevilsFoot:449         kgc:where   
25   DevilsFoot:413    kgc:infoSource   
245  DevilsFoot:463          kgc:what   
341  DevilsFoot:484         kgc:where   
228  DevilsFoot:459           kgc:why   
241  DevilsFoot:462    kgc:infoSource   
79   DevilsFoot:424    kgc:infoSource   
236  DevilsFoot:461          kgc:whom   
266  DevilsFoot:469       kgc:subject   
273  DevilsFoot:471       kgc:subject   
252  DevilsFoot:464    kgc:infoSource   
289  DevilsFoot:473          kgc:what   
246  DevilsFoot:463          kgc:what   
249  DevilsFoot:464       kgc:subject   
232  DevilsFoot:460    kgc:infoSource   
74   DevilsFoot:423          kgc:what   
262  DevilsFoot:468       kgc:subject   
247  DevilsFoot:463    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
297  DevilsFoot:473          kgc:what   
206  DevilsFoot:453    kgc:infoSource   
130  DevilsFoot:437          kgc:what   
264  DevilsFoot:468    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
324  DevilsFoot:480          kgc:what   
278  DevilsFoot:471    kgc:infoSource   
3    DevilsFoot:410    kgc:infoSource   
86   DevilsFoot:426          kgc:whom   
136         <bos_e>           <bos_r>   
328  DevilsFoot:481    kgc:infoSource   
311  DevilsFoot:476    kgc:infoSource   
298  DevilsFoot:473          kgc:what   
271  DevilsFoot:470    kgc:infoSource   
199  DevilsFoot:451         kgc:where   
288  DevilsFoot:473          kgc:what   
120  DevilsFoot:435         kgc:where   
148  DevilsFoot:440    kgc:infoSource   
230  DevilsFoot:460       kgc:subject   
326  DevilsFoot:481       kgc:subject   
224  DevilsFoot:458    kgc:infoSource   
81   DevilsFoot:425       kgc:subject   
73   DevilsFoot:423       kgc:subject   
152  DevilsFoot:441    kgc:infoSource   
267  DevilsFoot:469          kgc:what   
323  DevilsFoot:480       kgc:subject   
318  DevilsFoot:478    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
333  DevilsFoot:482          kgc:what   
72   DevilsFoot:423       kgc:subject   
70   DevilsFoot:422          kgc:what   
251  DevilsFoot:464          kgc:what   
170  DevilsFoot:445    kgc:infoSource   
142  DevilsFoot:439          kgc:when   
306  DevilsFoot:475    kgc:infoSource   
5    DevilsFoot:411    kgc:infoSource   
350  DevilsFoot:487       kgc:subject   
231  DevilsFoot:460          kgc:what   
62   DevilsFoot:421          kgc:when   
141  DevilsFoot:439          kgc:when   
295  DevilsFoot:473          kgc:what   
157  DevilsFoot:442    kgc:infoSource   
42          <bos_e>           <bos_r>   
35          <bos_e>           <bos_r>   
57   DevilsFoot:420          kgc:what   
117  DevilsFoot:434    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
270  DevilsFoot:470       kgc:subject   
216  DevilsFoot:456    kgc:infoSource   
38          <bos_e>           <bos_r>   
54          <bos_e>           <bos_r>   
28   DevilsFoot:414       kgc:subject   
226  DevilsFoot:459       kgc:subject   
16   DevilsFoot:412          kgc:what   
92   DevilsFoot:428          kgc:what   
41   DevilsFoot:417    kgc:infoSource   
223  DevilsFoot:458          kgc:what   
315  DevilsFoot:477    kgc:infoSource   
126  DevilsFoot:436    kgc:infoSource 

index=359, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


...

head          relation  \
357  DevilsFoot:489       kgc:subject   
55   DevilsFoot:420       kgc:subject   
167  DevilsFoot:445       kgc:subject   
363        <mask_e>          kgc:whom   
317  DevilsFoot:478       kgc:subject   
346  DevilsFoot:486       kgc:subject   
308  DevilsFoot:476       kgc:subject   
354  DevilsFoot:488       kgc:subject   
326  DevilsFoot:481       kgc:subject   
258  DevilsFoot:467       kgc:subject   
320  DevilsFoot:479       kgc:subject   
37   DevilsFoot:416          kgc:whom   
213  DevilsFoot:455          kgc:whom   
28   DevilsFoot:414       kgc:subject   
81   DevilsFoot:425       kgc:subject   
1    DevilsFoot:410       kgc:subject   
128  DevilsFoot:437       kgc:subject   
36   DevilsFoot:416       kgc:subject   
350  DevilsFoot:487       kgc:subject   
234  DevilsFoot:461       kgc:subject   
328  DevilsFoot:481    kgc:infoSource   
300  DevilsFoot:474       kgc:subject   
162  DevilsFoot:444       kgc:subject   
3    DevilsFoot:410    kgc:infoSource   
232  DevilsFoot:460    kgc:infoSource   
73   DevilsFoot:423       kgc:subject   
313  DevilsFoot:477       kgc:subject   
218  DevilsFoot:457       kgc:subject   
224  DevilsFoot:458    kgc:infoSource   
275  DevilsFoot:471          kgc:what   
123  DevilsFoot:436       kgc:subject   
220  DevilsFoot:457    kgc:infoSource   
288  DevilsFoot:473          kgc:what   
60   DevilsFoot:421       kgc:subject   
291  DevilsFoot:473          kgc:what   
273  DevilsFoot:471       kgc:subject   
283  DevilsFoot:472          kgc:whom   
137  DevilsFoot:439       kgc:subject   
267  DevilsFoot:469          kgc:what   
293  DevilsFoot:473          kgc:what   
243  DevilsFoot:463       kgc:subject   
290  DevilsFoot:473          kgc:what   
311  DevilsFoot:476    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
193  DevilsFoot:449    kgc:infoSource   
292  DevilsFoot:473          kgc:what   
304  DevilsFoot:475       kgc:subject   
208  DevilsFoot:454       kgc:subject   
315  DevilsFoot:477    kgc:infoSource   
230  DevilsFoot:460       kgc:subject   
135  DevilsFoot:438          kgc:whom   
83   DevilsFoot:426       kgc:subject   
249  DevilsFoot:464       kgc:subject   
364        <mask_e>       kgc:subject   
222  DevilsFoot:458       kgc:subject   
289  DevilsFoot:473          kgc:what   
260  DevilsFoot:467    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
5    DevilsFoot:411    kgc:infoSource   
186  DevilsFoot:448       kgc:subject   
172  DevilsFoot:446       kgc:subject   
294  DevilsFoot:473          kgc:what   
252  DevilsFoot:464    kgc:infoSource   
170  DevilsFoot:445    kgc:infoSource   
286  DevilsFoot:473       kgc:subject   
126  DevilsFoot:436    kgc:infoSource   
344  DevilsFoot:485    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
50   DevilsFoot:419       kgc:subject   
323  DevilsFoot:480       kgc:subject   
216  DevilsFoot:456    kgc:infoSource   
223  DevilsFoot:458          kgc:what   
335  DevilsFoot:482    kgc:infoSource   
287  DevilsFoot:473          kgc:what   
331  DevilsFoot:482       kgc:subject   
277  DevilsFoot:471          kgc:what   
237  DevilsFoot:461    kgc:infoSource   
124  DevilsFoot:436       kgc:subject   
75   DevilsFoot:423    kgc:infoSource   
266  DevilsFoot:469       kgc:subject   
271  DevilsFoot:470    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
206  DevilsFoot:453    kgc:infoSource   
122  DevilsFoot:436       kgc:subject   
165  DevilsFoot:444    kgc:infoSource   
296  DevilsFoot:473          kgc:what   
278  DevilsFoot:471    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
140  DevilsFoot:439    kgc:infoSource   
79   DevilsFoot:424    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
77   DevilsFoot:424       kgc:subject   
256  DevilsFoot:466       kgc:subject   
284  DevilsFoot:472    kgc:infoSource   
29   DevilsFoot:414    kgc:infoSource 

index=366, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
357  DevilsFoot:489       kgc:subject   
55   DevilsFoot:420       kgc:subject   
354  DevilsFoot:488       kgc:subject   
167  DevilsFoot:445       kgc:subject   
107  DevilsFoot:432       kgc:subject   
350  DevilsFoot:487       kgc:subject   
346  DevilsFoot:486       kgc:subject   
308  DevilsFoot:476       kgc:subject   
317  DevilsFoot:478       kgc:subject   
162  DevilsFoot:444       kgc:subject   
28   DevilsFoot:414       kgc:subject   
128  DevilsFoot:437       kgc:subject   
234  DevilsFoot:461       kgc:subject   
73   DevilsFoot:423       kgc:subject   
328  DevilsFoot:481    kgc:infoSource   
326  DevilsFoot:481       kgc:subject   
81   DevilsFoot:425       kgc:subject   
232  DevilsFoot:460    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
320  DevilsFoot:479       kgc:subject   
258  DevilsFoot:467       kgc:subject   
126  DevilsFoot:436    kgc:infoSource   
218  DevilsFoot:457       kgc:subject   
43   DevilsFoot:418       kgc:subject   
363        <mask_e>          kgc:whom   
311  DevilsFoot:476    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
123  DevilsFoot:436       kgc:subject   
293  DevilsFoot:473          kgc:what   
186  DevilsFoot:448       kgc:subject   
292  DevilsFoot:473          kgc:what   
273  DevilsFoot:471       kgc:subject   
237  DevilsFoot:461    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
315  DevilsFoot:477    kgc:infoSource   
252  DevilsFoot:464    kgc:infoSource   
79   DevilsFoot:424    kgc:infoSource   
288  DevilsFoot:473          kgc:what   
313  DevilsFoot:477       kgc:subject   
75   DevilsFoot:423    kgc:infoSource   
170  DevilsFoot:445    kgc:infoSource   
230  DevilsFoot:460       kgc:subject   
291  DevilsFoot:473          kgc:what   
137  DevilsFoot:439       kgc:subject   
41   DevilsFoot:417    kgc:infoSource   
124  DevilsFoot:436       kgc:subject   
29   DevilsFoot:414    kgc:infoSource   
300  DevilsFoot:474       kgc:subject   
243  DevilsFoot:463       kgc:subject   
289  DevilsFoot:473          kgc:what   
152  DevilsFoot:441    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
223  DevilsFoot:458          kgc:what   
290  DevilsFoot:473          kgc:what   
260  DevilsFoot:467    kgc:infoSource   
283  DevilsFoot:472          kgc:whom   
364        <mask_e>       kgc:subject   
1    DevilsFoot:410       kgc:subject   
60   DevilsFoot:421       kgc:subject   
140  DevilsFoot:439    kgc:infoSource   
3    DevilsFoot:410    kgc:infoSource   
294  DevilsFoot:473          kgc:what   
64   DevilsFoot:422       kgc:subject   
344  DevilsFoot:485    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
286  DevilsFoot:473       kgc:subject   
295  DevilsFoot:473          kgc:what   
135  DevilsFoot:438          kgc:whom   
131  DevilsFoot:437          kgc:whom   
181  DevilsFoot:446    kgc:infoSource   
249  DevilsFoot:464       kgc:subject   
148  DevilsFoot:440    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
117  DevilsFoot:434    kgc:infoSource   
52   DevilsFoot:419    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
296  DevilsFoot:473          kgc:what   
193  DevilsFoot:449    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
34   DevilsFoot:415    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
297  DevilsFoot:473          kgc:what   
206  DevilsFoot:453    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource   
37   DevilsFoot:416          kgc:whom   
5    DevilsFoot:411    kgc:infoSource   
36   DevilsFoot:416       kgc:subject   
172  DevilsFoot:446       kgc:subject   
157  DevilsFoot:442    kgc:infoSource   
287  DevilsFoot:473          kgc:what   
226  DevilsFoot:459       kgc:subject   
189  DevilsFoot:448    kgc:infoSource 

index=367, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
3    DevilsFoot:410    kgc:infoSource   
213  DevilsFoot:455          kgc:whom   
5    DevilsFoot:411    kgc:infoSource   
131  DevilsFoot:437          kgc:whom   
135  DevilsFoot:438          kgc:whom   
86   DevilsFoot:426          kgc:whom   
79   DevilsFoot:424    kgc:infoSource   
75   DevilsFoot:423    kgc:infoSource   
361        <mask_e>    kgc:infoSource   
85   DevilsFoot:426          kgc:what   
241  DevilsFoot:462    kgc:infoSource   
252  DevilsFoot:464    kgc:infoSource   
137  DevilsFoot:439       kgc:subject   
113  DevilsFoot:434       kgc:subject   
283  DevilsFoot:472          kgc:whom   
126  DevilsFoot:436    kgc:infoSource   
74   DevilsFoot:423          kgc:what   
134  DevilsFoot:438          kgc:whom   
193  DevilsFoot:449    kgc:infoSource   
237  DevilsFoot:461    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
142  DevilsFoot:439          kgc:when   
141  DevilsFoot:439          kgc:when   
107  DevilsFoot:432       kgc:subject   
109  DevilsFoot:433       kgc:subject   
37   DevilsFoot:416          kgc:whom   
62   DevilsFoot:421          kgc:when   
232  DevilsFoot:460    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
117  DevilsFoot:434    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
315  DevilsFoot:477    kgc:infoSource   
311  DevilsFoot:476    kgc:infoSource   
254  DevilsFoot:465       kgc:subject   
152  DevilsFoot:441    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
58   DevilsFoot:420          kgc:when   
206  DevilsFoot:453    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
156  DevilsFoot:442          kgc:whom   
346  DevilsFoot:486       kgc:subject   
83   DevilsFoot:426       kgc:subject   
200  DevilsFoot:451          kgc:when   
148  DevilsFoot:440    kgc:infoSource   
29   DevilsFoot:414    kgc:infoSource   
326  DevilsFoot:481       kgc:subject   
333  DevilsFoot:482          kgc:what   
236  DevilsFoot:461          kgc:whom   
169  DevilsFoot:445          kgc:whom   
25   DevilsFoot:413    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
243  DevilsFoot:463       kgc:subject   
41   DevilsFoot:417    kgc:infoSource   
249  DevilsFoot:464       kgc:subject   
170  DevilsFoot:445    kgc:infoSource   
61   DevilsFoot:421    kgc:infoSource   
128  DevilsFoot:437       kgc:subject   
103  DevilsFoot:431       kgc:subject   
157  DevilsFoot:442    kgc:infoSource   
363        <mask_e>          kgc:whom   
275  DevilsFoot:471          kgc:what   
224  DevilsFoot:458    kgc:infoSource   
140  DevilsFoot:439    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
271  DevilsFoot:470    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
189  DevilsFoot:448    kgc:infoSource   
34   DevilsFoot:415    kgc:infoSource   
334  DevilsFoot:482            kgc:to   
78   DevilsFoot:424          kgc:what   
186  DevilsFoot:448       kgc:subject   
52   DevilsFoot:419    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
313  DevilsFoot:477       kgc:subject   
105  DevilsFoot:431          kgc:what   
181  DevilsFoot:446    kgc:infoSource   
246  DevilsFoot:463          kgc:what   
234  DevilsFoot:461       kgc:subject   
251  DevilsFoot:464          kgc:what   
43   DevilsFoot:418       kgc:subject   
192  DevilsFoot:449         kgc:where   
258  DevilsFoot:467       kgc:subject   
67   DevilsFoot:422          kgc:what   
306  DevilsFoot:475    kgc:infoSource   
344  DevilsFoot:485    kgc:infoSource   
308  DevilsFoot:476       kgc:subject   
45   DevilsFoot:418    kgc:infoSource   
226  DevilsFoot:459       kgc:subject   
70   DevilsFoot:422          kgc:what   
92   DevilsFoot:428          kgc:what   
216  DevilsFoot:456    kgc:infoSource   
264  DevilsFoot:468    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
273  DevilsFoot:471       kgc:subject   
99   DevilsFoot:430       kgc:subject 

### DevilsFoot(悪魔の足跡2)
Who killed the victims? (criminal & explanation)
被害者: Mortimer
犯人: 
犯行動機: 恋人の敵

In [22]:
def do_devil2_pred():
    title = 'DevilsFoot'
    victim_name = 'Mortimer'
    killer_name = 'Sterndale'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil2_pred()
pass

2023-02-05 14:56:47 - INFO - 3560443472.py - 13 - The pred ranking about DevilsFoot:Sterndale is 254


predicate  \
ranking                                                      
0                                      word.predicate:kill   
1                                    word.predicate:return   
2                             DateTime:1883-04-01T15:00:00   
3                                     word.predicate:think   
4                                   word.predicate:examine   
5                                      word.predicate:find   
6                                      DevilsFoot:Roundhay   
7                            AbbeyGrange:Lady_Brackenstall   
8                                     word.predicate:guess   
9                                      word.predicate:lead   
10                                                 <bos_e>   
11                                   ACaseOfIdentity:Woman   
12                                     word.predicate:call   
13                                  SilverBlaze:Ned_Hunter   
14                                        CrookedMan:beast   
15                                    word.predicate:write   
16                                       word.predicate:go   
17                   AbbeyGrange:Burglary_team_of_Lewisham   
18                              SpeckledBand:1883-03-31T23   
19                            DateTime:1857-07-09T00:00:00   
20                                SilverBlaze:Silver_Blaze   
21                      ACaseOfIdentity:Hosmer_s_statement   
22                                         AllTitle:Holmes   
23                                     word.predicate:fall   
24                             DancingMen:1898-08-13T03:02   
25                                    word.predicate:shoot   
26                           SilverBlaze:Inspector_Gregory   
27                                    word.predicate:close   
28                                AbbeyGrange:cord_of_bell   
29                                   word.predicate:happen   
30                                     word.predicate:drop   
31                              word.predicate:participate   
32                                      word.predicate:hit   
33                                     word.predicate:meet   
34                                     word.predicate:dead   
35                        SilverBlaze:Wife_of_John_Straker   
36                            DateTime:1883-04-01T10:00:00   
37                                       CrookedMan:police   
38                                     word.predicate:want   
39                                     AbbeyGrange:Theresa   
40                                 AbbeyGrange:2_weeks_ago   
41                                         AllTitle:Watson   
42                                   word.predicate:turnOn   
43                                        CrookedMan:Henry   
44                                  word.predicate:request   
45                         SpeckledBand:mansion_of_Roylott   
46                                 AbbeyGrange:dining_room   
47                                    word.predicate:stand   
48                                      AbbeyGrange:police   
49                                        CrookedMan:Nancy   
50                         SilverBlaze:Door_of_the_stables   
51                               ResidentPatient:Young_man   
52                                    word.predicate:carry   
53                              SpeckledBand:1883-04-01T14   
54                                     word.predicate:lose   
55                                     word.predicate:hear   
56                                  word.predicate:confirm   
57                                   AbbeyGrange:Sideboard   
58                                        SpeckledBand:341   
59                                     DevilsFoot:Mortimer   
60                                 AbbeyGrange:Jack_Croker   
61                              SpeckledBand:1883-04-01T07   
62                                    word.predicate:exist   
63                 

index=358, triple=['DevilsFoot:489', 'kgc:hasPredicate', 'word.predicate:find'], attention list


head          relation  \
33   DevilsFoot:415         kgc:where   
48   DevilsFoot:418          kgc:time   
143  DevilsFoot:439          kgc:time   
155  DevilsFoot:442          kgc:what   
58   DevilsFoot:420          kgc:when   
218  DevilsFoot:457       kgc:subject   
276  DevilsFoot:471          kgc:what   
275  DevilsFoot:471          kgc:what   
53   DevilsFoot:419           kgc:why   
240  DevilsFoot:462          kgc:what   
75   DevilsFoot:423    kgc:infoSource   
367        <mask_e>         kgc:where   
277  DevilsFoot:471          kgc:what   
365        <mask_e>           kgc:why   
192  DevilsFoot:449         kgc:where   
29   DevilsFoot:414    kgc:infoSource   
40   DevilsFoot:417          kgc:what   
162  DevilsFoot:444       kgc:subject   
245  DevilsFoot:463          kgc:what   
25   DevilsFoot:413    kgc:infoSource   
341  DevilsFoot:484         kgc:where   
266  DevilsFoot:469       kgc:subject   
273  DevilsFoot:471       kgc:subject   
228  DevilsFoot:459           kgc:why   
289  DevilsFoot:473          kgc:what   
246  DevilsFoot:463          kgc:what   
79   DevilsFoot:424    kgc:infoSource   
252  DevilsFoot:464    kgc:infoSource   
236  DevilsFoot:461          kgc:whom   
241  DevilsFoot:462    kgc:infoSource   
249  DevilsFoot:464       kgc:subject   
262  DevilsFoot:468       kgc:subject   
74   DevilsFoot:423          kgc:what   
232  DevilsFoot:460    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
297  DevilsFoot:473          kgc:what   
260  DevilsFoot:467    kgc:infoSource   
206  DevilsFoot:453    kgc:infoSource   
130  DevilsFoot:437          kgc:what   
264  DevilsFoot:468    kgc:infoSource   
324  DevilsFoot:480          kgc:what   
278  DevilsFoot:471    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
271  DevilsFoot:470    kgc:infoSource   
298  DevilsFoot:473          kgc:what   
199  DevilsFoot:451         kgc:where   
326  DevilsFoot:481       kgc:subject   
136         <bos_e>           <bos_r>   
288  DevilsFoot:473          kgc:what   
328  DevilsFoot:481    kgc:infoSource   
323  DevilsFoot:480       kgc:subject   
311  DevilsFoot:476    kgc:infoSource   
86   DevilsFoot:426          kgc:whom   
3    DevilsFoot:410    kgc:infoSource   
230  DevilsFoot:460       kgc:subject   
120  DevilsFoot:435         kgc:where   
148  DevilsFoot:440    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
267  DevilsFoot:469          kgc:what   
333  DevilsFoot:482          kgc:what   
73   DevilsFoot:423       kgc:subject   
152  DevilsFoot:441    kgc:infoSource   
72   DevilsFoot:423       kgc:subject   
335  DevilsFoot:482    kgc:infoSource   
81   DevilsFoot:425       kgc:subject   
318  DevilsFoot:478    kgc:infoSource   
251  DevilsFoot:464          kgc:what   
220  DevilsFoot:457    kgc:infoSource   
70   DevilsFoot:422          kgc:what   
231  DevilsFoot:460          kgc:what   
295  DevilsFoot:473          kgc:what   
306  DevilsFoot:475    kgc:infoSource   
350  DevilsFoot:487       kgc:subject   
142  DevilsFoot:439          kgc:when   
170  DevilsFoot:445    kgc:infoSource   
5    DevilsFoot:411    kgc:infoSource   
270  DevilsFoot:470       kgc:subject   
62   DevilsFoot:421          kgc:when   
141  DevilsFoot:439          kgc:when   
157  DevilsFoot:442    kgc:infoSource   
42          <bos_e>           <bos_r>   
35          <bos_e>           <bos_r>   
57   DevilsFoot:420          kgc:what   
226  DevilsFoot:459       kgc:subject   
302  DevilsFoot:474    kgc:infoSource   
16   DevilsFoot:412          kgc:what   
117  DevilsFoot:434    kgc:infoSource   
38          <bos_e>           <bos_r>   
54          <bos_e>           <bos_r>   
216  DevilsFoot:456    kgc:infoSource   
92   DevilsFoot:428          kgc:what   
223  DevilsFoot:458          kgc:what   
331  DevilsFoot:482       kgc:subject   
28   DevilsFoot:414       kgc:subject   
15   DevilsFoot:412          kgc:what   
41   DevilsFoot:417    kgc:infoSource 

index=359, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


...

head          relation  \
357  DevilsFoot:489       kgc:subject   
55   DevilsFoot:420       kgc:subject   
167  DevilsFoot:445       kgc:subject   
317  DevilsFoot:478       kgc:subject   
346  DevilsFoot:486       kgc:subject   
308  DevilsFoot:476       kgc:subject   
326  DevilsFoot:481       kgc:subject   
354  DevilsFoot:488       kgc:subject   
320  DevilsFoot:479       kgc:subject   
28   DevilsFoot:414       kgc:subject   
258  DevilsFoot:467       kgc:subject   
213  DevilsFoot:455          kgc:whom   
81   DevilsFoot:425       kgc:subject   
350  DevilsFoot:487       kgc:subject   
37   DevilsFoot:416          kgc:whom   
1    DevilsFoot:410       kgc:subject   
36   DevilsFoot:416       kgc:subject   
328  DevilsFoot:481    kgc:infoSource   
128  DevilsFoot:437       kgc:subject   
232  DevilsFoot:460    kgc:infoSource   
234  DevilsFoot:461       kgc:subject   
3    DevilsFoot:410    kgc:infoSource   
300  DevilsFoot:474       kgc:subject   
162  DevilsFoot:444       kgc:subject   
275  DevilsFoot:471          kgc:what   
218  DevilsFoot:457       kgc:subject   
288  DevilsFoot:473          kgc:what   
73   DevilsFoot:423       kgc:subject   
313  DevilsFoot:477       kgc:subject   
290  DevilsFoot:473          kgc:what   
224  DevilsFoot:458    kgc:infoSource   
291  DevilsFoot:473          kgc:what   
220  DevilsFoot:457    kgc:infoSource   
292  DevilsFoot:473          kgc:what   
293  DevilsFoot:473          kgc:what   
267  DevilsFoot:469          kgc:what   
273  DevilsFoot:471       kgc:subject   
304  DevilsFoot:475       kgc:subject   
289  DevilsFoot:473          kgc:what   
123  DevilsFoot:436       kgc:subject   
230  DevilsFoot:460       kgc:subject   
311  DevilsFoot:476    kgc:infoSource   
60   DevilsFoot:421       kgc:subject   
5    DevilsFoot:411    kgc:infoSource   
208  DevilsFoot:454       kgc:subject   
214  DevilsFoot:455    kgc:infoSource   
283  DevilsFoot:472          kgc:whom   
260  DevilsFoot:467    kgc:infoSource   
222  DevilsFoot:458       kgc:subject   
363        <mask_e>          kgc:whom   
137  DevilsFoot:439       kgc:subject   
315  DevilsFoot:477    kgc:infoSource   
243  DevilsFoot:463       kgc:subject   
83   DevilsFoot:426       kgc:subject   
152  DevilsFoot:441    kgc:infoSource   
249  DevilsFoot:464       kgc:subject   
286  DevilsFoot:473       kgc:subject   
287  DevilsFoot:473          kgc:what   
193  DevilsFoot:449    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
294  DevilsFoot:473          kgc:what   
271  DevilsFoot:470    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
323  DevilsFoot:480       kgc:subject   
172  DevilsFoot:446       kgc:subject   
170  DevilsFoot:445    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
277  DevilsFoot:471          kgc:what   
252  DevilsFoot:464    kgc:infoSource   
75   DevilsFoot:423    kgc:infoSource   
266  DevilsFoot:469       kgc:subject   
216  DevilsFoot:456    kgc:infoSource   
331  DevilsFoot:482       kgc:subject   
135  DevilsFoot:438          kgc:whom   
223  DevilsFoot:458          kgc:what   
186  DevilsFoot:448       kgc:subject   
335  DevilsFoot:482    kgc:infoSource   
206  DevilsFoot:453    kgc:infoSource   
50   DevilsFoot:419       kgc:subject   
364        <mask_e>       kgc:subject   
126  DevilsFoot:436    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
344  DevilsFoot:485    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
79   DevilsFoot:424    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
298  DevilsFoot:473          kgc:what   
226  DevilsFoot:459       kgc:subject   
124  DevilsFoot:436       kgc:subject   
256  DevilsFoot:466       kgc:subject   
296  DevilsFoot:473          kgc:what   
237  DevilsFoot:461    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
295  DevilsFoot:473          kgc:what 

index=366, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
55   DevilsFoot:420       kgc:subject   
357  DevilsFoot:489       kgc:subject   
354  DevilsFoot:488       kgc:subject   
167  DevilsFoot:445       kgc:subject   
346  DevilsFoot:486       kgc:subject   
350  DevilsFoot:487       kgc:subject   
107  DevilsFoot:432       kgc:subject   
308  DevilsFoot:476       kgc:subject   
317  DevilsFoot:478       kgc:subject   
28   DevilsFoot:414       kgc:subject   
162  DevilsFoot:444       kgc:subject   
234  DevilsFoot:461       kgc:subject   
73   DevilsFoot:423       kgc:subject   
328  DevilsFoot:481    kgc:infoSource   
326  DevilsFoot:481       kgc:subject   
128  DevilsFoot:437       kgc:subject   
81   DevilsFoot:425       kgc:subject   
232  DevilsFoot:460    kgc:infoSource   
320  DevilsFoot:479       kgc:subject   
218  DevilsFoot:457       kgc:subject   
224  DevilsFoot:458    kgc:infoSource   
126  DevilsFoot:436    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
258  DevilsFoot:467       kgc:subject   
311  DevilsFoot:476    kgc:infoSource   
43   DevilsFoot:418       kgc:subject   
220  DevilsFoot:457    kgc:infoSource   
293  DevilsFoot:473          kgc:what   
292  DevilsFoot:473          kgc:what   
291  DevilsFoot:473          kgc:what   
288  DevilsFoot:473          kgc:what   
79   DevilsFoot:424    kgc:infoSource   
123  DevilsFoot:436       kgc:subject   
75   DevilsFoot:423    kgc:infoSource   
186  DevilsFoot:448       kgc:subject   
252  DevilsFoot:464    kgc:infoSource   
170  DevilsFoot:445    kgc:infoSource   
273  DevilsFoot:471       kgc:subject   
247  DevilsFoot:463    kgc:infoSource   
230  DevilsFoot:460       kgc:subject   
289  DevilsFoot:473          kgc:what   
313  DevilsFoot:477       kgc:subject   
290  DevilsFoot:473          kgc:what   
315  DevilsFoot:477    kgc:infoSource   
300  DevilsFoot:474       kgc:subject   
237  DevilsFoot:461    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
29   DevilsFoot:414    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
41   DevilsFoot:417    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
137  DevilsFoot:439       kgc:subject   
25   DevilsFoot:413    kgc:infoSource   
243  DevilsFoot:463       kgc:subject   
223  DevilsFoot:458          kgc:what   
124  DevilsFoot:436       kgc:subject   
3    DevilsFoot:410    kgc:infoSource   
283  DevilsFoot:472          kgc:whom   
294  DevilsFoot:473          kgc:what   
60   DevilsFoot:421       kgc:subject   
1    DevilsFoot:410       kgc:subject   
286  DevilsFoot:473       kgc:subject   
364        <mask_e>       kgc:subject   
278  DevilsFoot:471    kgc:infoSource   
64   DevilsFoot:422       kgc:subject   
295  DevilsFoot:473          kgc:what   
335  DevilsFoot:482    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
140  DevilsFoot:439    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
344  DevilsFoot:485    kgc:infoSource   
181  DevilsFoot:446    kgc:infoSource   
135  DevilsFoot:438          kgc:whom   
249  DevilsFoot:464       kgc:subject   
318  DevilsFoot:478    kgc:infoSource   
131  DevilsFoot:437          kgc:whom   
5    DevilsFoot:411    kgc:infoSource   
287  DevilsFoot:473          kgc:what   
296  DevilsFoot:473          kgc:what   
302  DevilsFoot:474    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
172  DevilsFoot:446       kgc:subject   
363        <mask_e>          kgc:whom   
193  DevilsFoot:449    kgc:infoSource   
52   DevilsFoot:419    kgc:infoSource   
297  DevilsFoot:473          kgc:what   
271  DevilsFoot:470    kgc:infoSource   
37   DevilsFoot:416          kgc:whom   
206  DevilsFoot:453    kgc:infoSource   
226  DevilsFoot:459       kgc:subject   
117  DevilsFoot:434    kgc:infoSource   
34   DevilsFoot:415    kgc:infoSource   
36   DevilsFoot:416       kgc:subject   
222  DevilsFoot:458       kgc:subject   
157  DevilsFoot:442    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource 

index=367, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
3    DevilsFoot:410    kgc:infoSource   
213  DevilsFoot:455          kgc:whom   
5    DevilsFoot:411    kgc:infoSource   
131  DevilsFoot:437          kgc:whom   
135  DevilsFoot:438          kgc:whom   
86   DevilsFoot:426          kgc:whom   
79   DevilsFoot:424    kgc:infoSource   
363        <mask_e>          kgc:whom   
75   DevilsFoot:423    kgc:infoSource   
74   DevilsFoot:423          kgc:what   
85   DevilsFoot:426          kgc:what   
252  DevilsFoot:464    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
113  DevilsFoot:434       kgc:subject   
126  DevilsFoot:436    kgc:infoSource   
283  DevilsFoot:472          kgc:whom   
137  DevilsFoot:439       kgc:subject   
193  DevilsFoot:449    kgc:infoSource   
134  DevilsFoot:438          kgc:whom   
237  DevilsFoot:461    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
361        <mask_e>    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
107  DevilsFoot:432       kgc:subject   
142  DevilsFoot:439          kgc:when   
141  DevilsFoot:439          kgc:when   
260  DevilsFoot:467    kgc:infoSource   
232  DevilsFoot:460    kgc:infoSource   
62   DevilsFoot:421          kgc:when   
109  DevilsFoot:433       kgc:subject   
318  DevilsFoot:478    kgc:infoSource   
117  DevilsFoot:434    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
311  DevilsFoot:476    kgc:infoSource   
315  DevilsFoot:477    kgc:infoSource   
37   DevilsFoot:416          kgc:whom   
58   DevilsFoot:420          kgc:when   
206  DevilsFoot:453    kgc:infoSource   
333  DevilsFoot:482          kgc:what   
348  DevilsFoot:486    kgc:infoSource   
200  DevilsFoot:451          kgc:when   
214  DevilsFoot:455    kgc:infoSource   
156  DevilsFoot:442          kgc:whom   
148  DevilsFoot:440    kgc:infoSource   
346  DevilsFoot:486       kgc:subject   
254  DevilsFoot:465       kgc:subject   
169  DevilsFoot:445          kgc:whom   
236  DevilsFoot:461          kgc:whom   
29   DevilsFoot:414    kgc:infoSource   
83   DevilsFoot:426       kgc:subject   
25   DevilsFoot:413    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
326  DevilsFoot:481       kgc:subject   
78   DevilsFoot:424          kgc:what   
249  DevilsFoot:464       kgc:subject   
271  DevilsFoot:470    kgc:infoSource   
170  DevilsFoot:445    kgc:infoSource   
243  DevilsFoot:463       kgc:subject   
61   DevilsFoot:421    kgc:infoSource   
41   DevilsFoot:417    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
275  DevilsFoot:471          kgc:what   
157  DevilsFoot:442    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
103  DevilsFoot:431       kgc:subject   
189  DevilsFoot:448    kgc:infoSource   
128  DevilsFoot:437       kgc:subject   
268  DevilsFoot:469    kgc:infoSource   
186  DevilsFoot:448       kgc:subject   
140  DevilsFoot:439    kgc:infoSource   
192  DevilsFoot:449         kgc:where   
34   DevilsFoot:415    kgc:infoSource   
334  DevilsFoot:482            kgc:to   
251  DevilsFoot:464          kgc:what   
258  DevilsFoot:467       kgc:subject   
246  DevilsFoot:463          kgc:what   
313  DevilsFoot:477       kgc:subject   
70   DevilsFoot:422          kgc:what   
181  DevilsFoot:446    kgc:infoSource   
226  DevilsFoot:459       kgc:subject   
52   DevilsFoot:419    kgc:infoSource   
43   DevilsFoot:418       kgc:subject   
67   DevilsFoot:422          kgc:what   
234  DevilsFoot:461       kgc:subject   
306  DevilsFoot:475    kgc:infoSource   
92   DevilsFoot:428          kgc:what   
264  DevilsFoot:468    kgc:infoSource   
308  DevilsFoot:476       kgc:subject   
344  DevilsFoot:485    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource   
105  DevilsFoot:431          kgc:what   
284  DevilsFoot:472    kgc:infoSource   
273  DevilsFoot:471       kgc:subject   
267  DevilsFoot:469          kgc:what 

### AbbeyGrange(僧坊荘園)
Who killed Lord Blackenstall? (criminal & explanation)
被害者: Sir_Eustace_Brackenstall
犯人: 
犯行動機:

In [23]:
def do_AbbeyGrange_pred():
    title = 'AbbeyGrange'
    victim_name = 'Sir_Eustace_Brackenstall'
    killer_name = 'Jack_Croker'
    last_index = 414
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_AbbeyGrange_pred()
pass

2023-02-05 14:56:48 - INFO - 3560443472.py - 13 - The pred ranking about AbbeyGrange:Jack_Croker is 1


predicate  \
ranking                                       
0                       word.predicate:kill   
1                      word.predicate:think   
2              DateTime:1883-04-01T15:00:00   
3                      word.predicate:stand   
4                       word.predicate:meet   
5                    word.predicate:examine   
6                        word.predicate:hit   
7                      word.predicate:guess   
8                     ACaseOfIdentity:Woman   
9                     word.predicate:return   
10                                  <bos_e>   
11               SpeckledBand:1883-03-31T23   
12                       AbbeyGrange:police   
13       ACaseOfIdentity:Hosmer_s_statement   
14                      DevilsFoot:Roundhay   
15                 SilverBlaze:Silver_Blaze   
16                   SilverBlaze:Ned_Hunter   
17                         CrookedMan:beast   
18                          AllTitle:Holmes   
19                  AbbeyGrange:Jack_Croker   

                                          whom                    subject  \
ranking                                                                     
0                AbbeyGrange:Lady_Brackenstall                    <bos_e>   
1         AbbeyGrange:Sir_Eustace_Brackenstall    AbbeyGrange:Jack_Croker   
2                          DevilsFoot:Roundhay            AllTitle:Holmes   
3                         word.predicate:think         AbbeyGrange:police   
4                          word.predicate:feel        DevilsFoot:Roundhay   
5                                      <bos_e>       word.predicate:think   
6                          word.predicate:meet   SilverBlaze:John_Straker   
7                           word.predicate:say           CrookedMan:Nancy   
8                              AllTitle:Watson     word.predicate:notHave   
9                             CrookedMan:Henry        word.predicate:know   
10                         word.predicate:find            AllTitle:Watson   
11       AbbeyGrange:Burglary_team_of_Lewisham          DevilsFoot:window   
12                          AbbeyGrange:police          word.predicate:go   
13                           CrookedMan:police        word.predicate:wear   
14                      ACaseOfIdentity:Hosmer      word.predicate:happen   
15                DateTime:1883-04-01T15:00:00  SilverBlaze:two_young_men   
16                             DevilsFoot:Owen        DevilsFoot:Mortimer   
17                  ACaseOfIdentity:Sutherland          DevilsFoot:Porter   
18                            CrookedMan:Nancy  DevilsFoot:Doctor_Richard   
19                      word.predicate:examine       SilverBlaze:Criminal   

                                          why                       what  \
ranking                                                                    
0                                     <bos_e>                    <bos_e>   
1        ACaseOfIdentity:mother_of_Sutherland   SilverBlaze:John_Straker   
2                         word.predicate:wear    AbbeyGrange:Jack_Croker   
3                  ACaseOfIdentity:Sutherland        DevilsFoot:Roundhay   
4                    SilverBlaze:John_Straker          word.predicate:go   
5                      ACaseOfIdentity:letter     SilverBlaze:Ned_Hunter   
6                        word.predicate:leave        word.predicate:find   
7                          SilverBlaze:stable           CrookedMan:Nancy   
8                    SilverBlaze:Edith_Baxter       word.predicate:think   
9                           DevilsFoot:Porter        word.predicate:know   
10                       word.predicate:upset     word.predicate:notHave   
11                           CrookedMan:Nancy            AllTitle:Watson   
12                  DevilsFoot:Doctor_Richard         SpeckledBand:Helen   
13                        word.predicate:come        word.predicate:meet   
14                            DevilsFoot:lamp        DevilsFoot:Mortimer   
15          

index=343, triple=['AbbeyGrange:414', 'kgc:hasPredicate', 'word.predicate:cannotFind'], attention list


head          relation  \
317   AbbeyGrange:407    kgc:infoSource   
239   AbbeyGrange:390           kgc:why   
330   AbbeyGrange:411       kgc:subject   
257           <bos_e>           <bos_r>   
116           <bos_e>           <bos_r>   
290   AbbeyGrange:401    kgc:infoSource   
183           <bos_e>           <bos_r>   
191   AbbeyGrange:378          kgc:what   
228   AbbeyGrange:388       kgc:subject   
240           <bos_e>           <bos_r>   
112           <bos_e>           <bos_r>   
120           <bos_e>           <bos_r>   
304           <bos_e>           <bos_r>   
123           <bos_e>           <bos_r>   
320   AbbeyGrange:408          kgc:what   
282   AbbeyGrange:400       kgc:subject   
289   AbbeyGrange:401          kgc:what   
312   AbbeyGrange:406          kgc:what   
260           <bos_e>           <bos_r>   
57            <bos_e>           <bos_r>   
14            <bos_e>           <bos_r>   
285   AbbeyGrange:400    kgc:infoSource   
319   AbbeyGrange:408       kgc:subject   
187   AbbeyGrange:377    kgc:infoSource   
135           <bos_e>           <bos_r>   
188           <bos_e>           <bos_r>   
97            <bos_e>           <bos_r>   
72            <bos_e>           <bos_r>   
235           <bos_e>           <bos_r>   
340   AbbeyGrange:413    kgc:infoSource   
313   AbbeyGrange:406    kgc:infoSource   
309           <bos_e>           <bos_r>   
310   AbbeyGrange:406       kgc:subject   
346          <mask_e>    kgc:infoSource   
339   AbbeyGrange:413          kgc:what   
263           <bos_e>           <bos_r>   
107           <bos_e>           <bos_r>   
314           <bos_e>           <bos_r>   
127           <bos_e>           <bos_r>   
0             <bos_e>           <bos_r>   
102           <bos_e>           <bos_r>   
315   AbbeyGrange:407       kgc:subject   
121   AbbeyGrange:362    kgc:infoSource   
119   AbbeyGrange:361    kgc:infoSource   
9             <bos_e>           <bos_r>   
269   AbbeyGrange:397          kgc:what   
280  AbbeyGrange:399a    kgc:infoSource   
182   AbbeyGrange:376           kgc:why   
345           <bos_e>           <bos_r>   
139           <bos_e>           <bos_r>   
208   AbbeyGrange:382    kgc:infoSource   
284   AbbeyGrange:400          kgc:what   
93            <bos_e>           <bos_r>   
151   AbbeyGrange:369       kgc:subject   
274           <bos_e>           <bos_r>   
307   AbbeyGrange:405    kgc:infoSource   
299           <bos_e>           <bos_r>   
266           <bos_e>           <bos_r>   
318           <bos_e>           <bos_r>   
5             <bos_e>           <bos_r>   
61            <bos_e>           <bos_r>   
336           <bos_e>           <bos_r>   
51            <bos_e>           <bos_r>   
199   AbbeyGrange:380    kgc:infoSource   
321           <bos_e>           <bos_r>   
181   AbbeyGrange:376    kgc:infoSource   
155   AbbeyGrange:369    kgc:infoSource   
204   AbbeyGrange:381    kgc:infoSource   
206   AbbeyGrange:382       kgc:subject   
246           <bos_e>           <bos_r>   
68            <bos_e>           <bos_r>   
131           <bos_e>           <bos_r>   
341           <bos_e>           <bos_r>   
125   AbbeyGrange:363    kgc:infoSource   
19            <bos_e>           <bos_r>   
287   AbbeyGrange:401       kgc:subject   
92    AbbeyGrange:355    kgc:infoSource   
178           <bos_e>           <bos_r>   
89            <bos_e>           <bos_r>   
278           <bos_e>           <bos_r>   
325           <bos_e>           <bos_r>   
298   AbbeyGrange:403    kgc:infoSource   
76            <bos_e>           <bos_r>   
201   AbbeyGrange:381       kgc:subject   
271           <bos_e>           <bos_r>   
148   AbbeyGrange:368    kgc:infoSource   
189   AbbeyGrange:378       kgc:subject   
175           <bos_e>           <bos_r>   
12    AbbeyGrange:337    kgc:infoSource   
332   AbbeyGrange:411          kgc:what   
205           <bos_e>           <bos_r>   
227           <bos_e>           <bos_r>   
136   AbbeyGrange:

index=344, triple=['AbbeyGrange:414', 'kgc:what', 'AbbeyGrange:False_charge_person'], attention list


...

head          relation  \
13    AbbeyGrange:337           kgc:why   
255   AbbeyGrange:393          kgc:when   
303   AbbeyGrange:404           kgc:why   
308   AbbeyGrange:405           kgc:why   
290   AbbeyGrange:401    kgc:infoSource   
153   AbbeyGrange:369          kgc:what   
182   AbbeyGrange:376           kgc:why   
256   AbbeyGrange:393           kgc:why   
317   AbbeyGrange:407    kgc:infoSource   
18    AbbeyGrange:338          kgc:what   
280  AbbeyGrange:399a    kgc:infoSource   
273   AbbeyGrange:398    kgc:infoSource   
313   AbbeyGrange:406    kgc:infoSource   
298   AbbeyGrange:403    kgc:infoSource   
119   AbbeyGrange:361    kgc:infoSource   
121   AbbeyGrange:362    kgc:infoSource   
320   AbbeyGrange:408          kgc:what   
125   AbbeyGrange:363    kgc:infoSource   
92    AbbeyGrange:355    kgc:infoSource   
339   AbbeyGrange:413          kgc:what   
340   AbbeyGrange:413    kgc:infoSource   
187   AbbeyGrange:377    kgc:infoSource   
310   AbbeyGrange:406       kgc:subject   
315   AbbeyGrange:407       kgc:subject   
11    AbbeyGrange:337   kgc:hasProperty   
285   AbbeyGrange:400    kgc:infoSource   
348          <mask_e>          kgc:whom   
88    AbbeyGrange:354          kgc:what   
346          <mask_e>    kgc:infoSource   
344   AbbeyGrange:414          kgc:what   
218   AbbeyGrange:385    kgc:infoSource   
332   AbbeyGrange:411          kgc:what   
203   AbbeyGrange:381          kgc:what   
208   AbbeyGrange:382    kgc:infoSource   
302   AbbeyGrange:404          kgc:whom   
57            <bos_e>           <bos_r>   
105   AbbeyGrange:358          kgc:what   
184   AbbeyGrange:377       kgc:subject   
96    AbbeyGrange:356    kgc:infoSource   
180   AbbeyGrange:376          kgc:what   
183           <bos_e>           <bos_r>   
309           <bos_e>           <bos_r>   
120           <bos_e>           <bos_r>   
324   AbbeyGrange:409    kgc:infoSource   
307   AbbeyGrange:405    kgc:infoSource   
12    AbbeyGrange:337    kgc:infoSource   
0             <bos_e>           <bos_r>   
147   AbbeyGrange:368          kgc:what   
314           <bos_e>           <bos_r>   
8     AbbeyGrange:336          kgc:what   
282   AbbeyGrange:400       kgc:subject   
123           <bos_e>           <bos_r>   
312   AbbeyGrange:406          kgc:what   
174   AbbeyGrange:374          kgc:what   
116           <bos_e>           <bos_r>   
44    AbbeyGrange:344           kgc:why   
91    AbbeyGrange:355   kgc:hasProperty   
289   AbbeyGrange:401          kgc:what   
263           <bos_e>           <bos_r>   
127           <bos_e>           <bos_r>   
134   AbbeyGrange:365           kgc:why   
305   AbbeyGrange:405       kgc:subject   
111   AbbeyGrange:359    kgc:infoSource   
204   AbbeyGrange:381    kgc:infoSource   
336           <bos_e>           <bos_r>   
270   AbbeyGrange:397    kgc:infoSource   
245   AbbeyGrange:391          kgc:when   
112           <bos_e>           <bos_r>   
155   AbbeyGrange:369    kgc:infoSource   
258   AbbeyGrange:394       kgc:subject   
24    AbbeyGrange:340          kgc:what   
188           <bos_e>           <bos_r>   
297   AbbeyGrange:403          kgc:whom   
9             <bos_e>           <bos_r>   
240           <bos_e>           <bos_r>   
342   AbbeyGrange:414       kgc:subject   
239   AbbeyGrange:390           kgc:why   
181   AbbeyGrange:376    kgc:infoSource   
257           <bos_e>           <bos_r>   
318           <bos_e>           <bos_r>   
304           <bos_e>           <bos_r>   
151   AbbeyGrange:369       kgc:subject   
171   AbbeyGrange:373    kgc:infoSource   
337   AbbeyGrange:413       kgc:subject   
300   AbbeyGrange:404       kgc:subject   
321           <bos_e>           <bos_r>   
228   AbbeyGrange:388       kgc:subject   
199   AbbeyGrange:380    kgc:infoSource   
231   AbbeyGrange:388    kgc:infoSource   
266           <bos_e>           <bos_r>   
79    AbbeyGrange:352    kgc:infoSource   
261   AbbeyGrange:395       kgc:subject   
252   AbbeyGrange:

index=351, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
319   AbbeyGrange:408       kgc:subject   
334   AbbeyGrange:412       kgc:subject   
342   AbbeyGrange:414       kgc:subject   
258   AbbeyGrange:394       kgc:subject   
261   AbbeyGrange:395       kgc:subject   
300   AbbeyGrange:404       kgc:subject   
292   AbbeyGrange:402       kgc:subject   
224   AbbeyGrange:387       kgc:subject   
236   AbbeyGrange:390       kgc:subject   
282   AbbeyGrange:400       kgc:subject   
310   AbbeyGrange:406       kgc:subject   
173   AbbeyGrange:374       kgc:subject   
264   AbbeyGrange:396       kgc:subject   
252   AbbeyGrange:393       kgc:subject   
184   AbbeyGrange:377       kgc:subject   
315   AbbeyGrange:407       kgc:subject   
119   AbbeyGrange:361    kgc:infoSource   
298   AbbeyGrange:403    kgc:infoSource   
326   AbbeyGrange:410       kgc:subject   
125   AbbeyGrange:363    kgc:infoSource   
228   AbbeyGrange:388       kgc:subject   
233   AbbeyGrange:389       kgc:subject   
255   AbbeyGrange:393          kgc:when   
163   AbbeyGrange:371    kgc:infoSource   
208   AbbeyGrange:382    kgc:infoSource   
171   AbbeyGrange:373    kgc:infoSource   
121   AbbeyGrange:362    kgc:infoSource   
256   AbbeyGrange:393           kgc:why   
10    AbbeyGrange:337       kgc:subject   
187   AbbeyGrange:377    kgc:infoSource   
330   AbbeyGrange:411       kgc:subject   
290   AbbeyGrange:401    kgc:infoSource   
8     AbbeyGrange:336          kgc:what   
6     AbbeyGrange:336       kgc:subject   
231   AbbeyGrange:388    kgc:infoSource   
60    AbbeyGrange:347    kgc:infoSource   
204   AbbeyGrange:381    kgc:infoSource   
273   AbbeyGrange:398    kgc:infoSource   
180   AbbeyGrange:376          kgc:what   
167   AbbeyGrange:372    kgc:infoSource   
199   AbbeyGrange:380    kgc:infoSource   
307   AbbeyGrange:405    kgc:infoSource   
350          <mask_e>           kgc:why   
130   AbbeyGrange:364    kgc:infoSource   
339   AbbeyGrange:413          kgc:what   
312   AbbeyGrange:406          kgc:what   
346          <mask_e>    kgc:infoSource   
73    AbbeyGrange:351       kgc:subject   
150   AbbeyGrange:369       kgc:subject   
63    AbbeyGrange:348    kgc:infoSource   
108   AbbeyGrange:359       kgc:subject   
322   AbbeyGrange:409       kgc:subject   
267   AbbeyGrange:397       kgc:subject   
189   AbbeyGrange:378       kgc:subject   
92    AbbeyGrange:355    kgc:infoSource   
70    AbbeyGrange:350       kgc:subject   
1     AbbeyGrange:335       kgc:subject   
344   AbbeyGrange:414          kgc:what   
151   AbbeyGrange:369       kgc:subject   
12    AbbeyGrange:337    kgc:infoSource   
49    AbbeyGrange:345    kgc:infoSource   
114   AbbeyGrange:360    kgc:infoSource   
79    AbbeyGrange:352    kgc:infoSource   
143   AbbeyGrange:367    kgc:infoSource   
243   AbbeyGrange:391          kgc:what   
332   AbbeyGrange:411          kgc:what   
181   AbbeyGrange:376    kgc:infoSource   
111   AbbeyGrange:359    kgc:infoSource   
349          <mask_e>       kgc:subject   
244   AbbeyGrange:391    kgc:infoSource   
155   AbbeyGrange:369    kgc:infoSource   
25    AbbeyGrange:340    kgc:infoSource   
146   AbbeyGrange:368       kgc:subject   
145   AbbeyGrange:368       kgc:subject   
245   AbbeyGrange:391          kgc:when   
4     AbbeyGrange:335    kgc:infoSource   
157   AbbeyGrange:370       kgc:subject   
16    AbbeyGrange:338       kgc:subject   
250  AbbeyGrange:392a          kgc:what   
75    AbbeyGrange:351    kgc:infoSource   
106   AbbeyGrange:358    kgc:infoSource   
136   AbbeyGrange:366       kgc:subject   
337   AbbeyGrange:413       kgc:subject   
43    AbbeyGrange:344    kgc:infoSource   
21    AbbeyGrange:339       kgc:subject   
148   AbbeyGrange:368    kgc:infoSource   
133   AbbeyGrange:365    kgc:infoSource   
69    AbbeyGrange:350       kgc:subject   
20    AbbeyGrange:339       kgc:subject   
147   AbbeyGrange:368          kgc:what   
117   AbbeyGrange:361       kgc:subject   
287   AbbeyGrange:401       kgc:subject   
15    AbbeyGrange:

index=352, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
315   AbbeyGrange:407       kgc:subject   
310   AbbeyGrange:406       kgc:subject   
282   AbbeyGrange:400       kgc:subject   
319   AbbeyGrange:408       kgc:subject   
267   AbbeyGrange:397       kgc:subject   
236   AbbeyGrange:390       kgc:subject   
258   AbbeyGrange:394       kgc:subject   
313   AbbeyGrange:406    kgc:infoSource   
252   AbbeyGrange:393       kgc:subject   
228   AbbeyGrange:388       kgc:subject   
255   AbbeyGrange:393          kgc:when   
171   AbbeyGrange:373    kgc:infoSource   
317   AbbeyGrange:407    kgc:infoSource   
285   AbbeyGrange:400    kgc:infoSource   
290   AbbeyGrange:401    kgc:infoSource   
73    AbbeyGrange:351       kgc:subject   
224   AbbeyGrange:387       kgc:subject   
298   AbbeyGrange:403    kgc:infoSource   
119   AbbeyGrange:361    kgc:infoSource   
270   AbbeyGrange:397    kgc:infoSource   
125   AbbeyGrange:363    kgc:infoSource   
342   AbbeyGrange:414       kgc:subject   
108   AbbeyGrange:359       kgc:subject   
280  AbbeyGrange:399a    kgc:infoSource   
218   AbbeyGrange:385    kgc:infoSource   
334   AbbeyGrange:412       kgc:subject   
261   AbbeyGrange:395       kgc:subject   
70    AbbeyGrange:350       kgc:subject   
184   AbbeyGrange:377       kgc:subject   
121   AbbeyGrange:362    kgc:infoSource   
92    AbbeyGrange:355    kgc:infoSource   
130   AbbeyGrange:364    kgc:infoSource   
264   AbbeyGrange:396       kgc:subject   
163   AbbeyGrange:371    kgc:infoSource   
340   AbbeyGrange:413    kgc:infoSource   
133   AbbeyGrange:365    kgc:infoSource   
348          <mask_e>          kgc:whom   
208   AbbeyGrange:382    kgc:infoSource   
273   AbbeyGrange:398    kgc:infoSource   
12    AbbeyGrange:337    kgc:infoSource   
25    AbbeyGrange:340    kgc:infoSource   
204   AbbeyGrange:381    kgc:infoSource   
256   AbbeyGrange:393           kgc:why   
330   AbbeyGrange:411       kgc:subject   
300   AbbeyGrange:404       kgc:subject   
167   AbbeyGrange:372    kgc:infoSource   
69    AbbeyGrange:350       kgc:subject   
143   AbbeyGrange:367    kgc:infoSource   
173   AbbeyGrange:374       kgc:subject   
84    AbbeyGrange:353    kgc:infoSource   
49    AbbeyGrange:345    kgc:infoSource   
6     AbbeyGrange:336       kgc:subject   
187   AbbeyGrange:377    kgc:infoSource   
13    AbbeyGrange:337           kgc:why   
199   AbbeyGrange:380    kgc:infoSource   
43    AbbeyGrange:344    kgc:infoSource   
10    AbbeyGrange:337       kgc:subject   
346          <mask_e>    kgc:infoSource   
292   AbbeyGrange:402       kgc:subject   
148   AbbeyGrange:368    kgc:infoSource   
79    AbbeyGrange:352    kgc:infoSource   
243   AbbeyGrange:391          kgc:what   
308   AbbeyGrange:405           kgc:why   
322   AbbeyGrange:409       kgc:subject   
181   AbbeyGrange:376    kgc:infoSource   
245   AbbeyGrange:391          kgc:when   
136   AbbeyGrange:366       kgc:subject   
4     AbbeyGrange:335    kgc:infoSource   
349          <mask_e>       kgc:subject   
307   AbbeyGrange:405    kgc:infoSource   
151   AbbeyGrange:369       kgc:subject   
155   AbbeyGrange:369    kgc:infoSource   
16    AbbeyGrange:338       kgc:subject   
1     AbbeyGrange:335       kgc:subject   
63    AbbeyGrange:348    kgc:infoSource   
8     AbbeyGrange:336          kgc:what   
117   AbbeyGrange:361       kgc:subject   
150   AbbeyGrange:369       kgc:subject   
44    AbbeyGrange:344           kgc:why   
337   AbbeyGrange:413       kgc:subject   
67    AbbeyGrange:349    kgc:infoSource   
56    AbbeyGrange:346          kgc:when   
18    AbbeyGrange:338          kgc:what   
305   AbbeyGrange:405       kgc:subject   
60    AbbeyGrange:347    kgc:infoSource   
239   AbbeyGrange:390           kgc:why   
189   AbbeyGrange:378       kgc:subject   
231   AbbeyGrange:388    kgc:infoSource   
157   AbbeyGrange:370       kgc:subject   
182   AbbeyGrange:376           kgc:why   
96    AbbeyGrange:356    kgc:infoSource   
46    AbbeyGrange:345       kgc:subject   
250  AbbeyGrange:3

### 入院患者
Who killed Blessington? (criminal & explanation)
被害者: Blessington
犯人: 3人
犯行動機:

In [24]:
def do_ResidentPatient_pred():
    title = 'ResidentPatient'
    victim_name = 'Blessington'
    killer_name = ''
    last_index = 324
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_ResidentPatient_pred()

2023-02-05 14:56:49 - INFO - 3560443472.py - 13 - The pred ranking about ResidentPatient: is -1


predicate  \
ranking                                 
0                 word.predicate:kill   
1                 word.predicate:call   
2                   word.predicate:go   
3              word.predicate:examine   
4               word.predicate:return   
5        DateTime:1857-07-09T00:00:00   
6                 DevilsFoot:Roundhay   
7                    CrookedMan:beast   
8              SilverBlaze:Ned_Hunter   
9                word.predicate:close   
10               word.predicate:think   
11           SilverBlaze:Silver_Blaze   
12                word.predicate:drop   
13                word.predicate:live   
14               word.predicate:shoot   
15       DateTime:1883-04-01T10:00:00   
16           AbbeyGrange:cord_of_bell   
17                word.predicate:want   
18                word.predicate:lead   
19                    DevilsFoot:Owen   

                                             whom  \
ranking                                             
0                     ResidentPatient:Blessington   
1                             DevilsFoot:Roundhay   
2                        SilverBlaze:Silver_Blaze   
3                                 DevilsFoot:Owen   
4                     ResidentPatient:Elderly_man   
5                             DevilsFoot:Mortimer   
6                         AbbeyGrange:Jack_Croker   
7                       DevilsFoot:Doctor_Richard   
8                 ResidentPatient:Percy_Trevelyan   
9        ResidentPatient:Worthington_bank_Robbers   
10                       SilverBlaze:Colonel_Ross   
11                                        <bos_e>   
12                               CrookedMan:Henry   
13                               CrookedMan:Nancy   
14                           word.predicate:visit   
15                  SilverBlaze:Inspector_Gregory   
16                              CrookedMan:police   
17                           word.predicate:guess   
18                  AbbeyGrange:Thought_of_Holmes   
19                   SpeckledBand:VentilationHole   

                                          subject  \
ranking                                             
0                                         <bos_e>   
1                     ResidentPatient:Blessington   
2                        SilverBlaze:Silver_Blaze   
3                             DevilsFoot:Mortimer   
4                        SilverBlaze:John_Straker   
5                             DevilsFoot:Roundhay   
6                         AbbeyGrange:Jack_Croker   
7                          SilverBlaze:Ned_Hunter   
8                        SilverBlaze:Colonel_Ross   
9                             word.predicate:know   
10                    ResidentPatient:Elderly_man   
11                               CrookedMan:Nancy   
12                              word.predicate:go   
13       ResidentPatient:Worthington_bank_Robbers   
14                ResidentPatient:Percy_Trevelyan   
15                      DevilsFoot:Doctor_Richard   
16                      SilverBlaze:two_young_men   
17                             SpeckledBand:Helen   
18                                DevilsFoot:Owen   
19                           word.predicate:guess   

                                              why  \
ranking                                             
0                                         <bos_e>   
1                             DevilsFoot:Roundhay   
2                     ResidentPatient:Blessington   
3                             DevilsFoot:Mortimer   
4                        SilverBlaze:Colonel_Ross   
5                          SilverBlaze:Ned_Hunter   
6                        SilverBlaze:Silver_Blaze   
7                    SpeckledBand:Julia_s_bedroom   
8                                CrookedMan:Nancy   
9                    SpeckledBand:VentilationHole   
10                          word.predicate:asleep   
11                            word.predicate:find   
12       ResidentPatient:Worthington_bank_Robbers

index=343, triple=['ResidentPatient:324', 'kgc:hasProperty', 'word.predicate:want'], attention list


head          relation  \
248   ResidentPatient:301          kgc:time   
302   ResidentPatient:315  kgc:hasPredicate   
344   ResidentPatient:324          kgc:what   
293   ResidentPatient:312          kgc:what   
343   ResidentPatient:324   kgc:hasProperty   
152   ResidentPatient:279          kgc:what   
340   ResidentPatient:323          kgc:what   
292   ResidentPatient:312   kgc:hasProperty   
246   ResidentPatient:301  kgc:hasPredicate   
162   ResidentPatient:282  kgc:hasPredicate   
45    ResidentPatient:256  kgc:hasPredicate   
291   ResidentPatient:312       kgc:subject   
24    ResidentPatient:252  kgc:hasPredicate   
347              <mask_e>  kgc:hasPredicate   
275   ResidentPatient:308  kgc:hasPredicate   
329   ResidentPatient:320  kgc:hasPredicate   
72    ResidentPatient:263   kgc:hasProperty   
86    ResidentPatient:266          kgc:time   
339   ResidentPatient:323   kgc:hasProperty   
134   ResidentPatient:274  kgc:hasPredicate   
94    ResidentPatient:268   kgc:hasProperty   
268  ResidentPatient:305a  kgc:hasPredicate   
73    ResidentPatient:263          kgc:what   
254   ResidentPatient:302          kgc:time   
194   ResidentPatient:290  kgc:hasPredicate   
231   ResidentPatient:298  kgc:hasPredicate   
67    ResidentPatient:262          kgc:what   
269  ResidentPatient:305a          kgc:what   
42    ResidentPatient:255          kgc:time   
69    ResidentPatient:262          kgc:what   
312   ResidentPatient:317  kgc:hasPredicate   
242   ResidentPatient:300  kgc:hasPredicate   
54    ResidentPatient:258  kgc:hasPredicate   
285   ResidentPatient:310   kgc:hasProperty   
202   ResidentPatient:292          kgc:what   
251   ResidentPatient:302  kgc:hasPredicate   
68    ResidentPatient:262          kgc:what   
65    ResidentPatient:262          kgc:what   
31    ResidentPatient:253          kgc:time   
49    ResidentPatient:257  kgc:hasPredicate   
66    ResidentPatient:262          kgc:what   
7     ResidentPatient:247  kgc:hasPredicate   
206   ResidentPatient:293  kgc:hasPredicate   
96    ResidentPatient:269  kgc:hasPredicate   
55    ResidentPatient:258          kgc:what   
306   ResidentPatient:316  kgc:hasPredicate   
71    ResidentPatient:263       kgc:subject   
100   ResidentPatient:270  kgc:hasPredicate   
335   ResidentPatient:322   kgc:hasProperty   
317   ResidentPatient:318   kgc:hasProperty   
336   ResidentPatient:322          kgc:what   
299   ResidentPatient:314  kgc:hasPredicate   
62    ResidentPatient:261   kgc:hasProperty   
272   ResidentPatient:306  kgc:hasPredicate   
234   ResidentPatient:298          kgc:what   
56    ResidentPatient:258          kgc:what   
97    ResidentPatient:269          kgc:what   
50    ResidentPatient:257          kgc:what   
257   ResidentPatient:303  kgc:hasPredicate   
232   ResidentPatient:298          kgc:what   
175   ResidentPatient:285  kgc:hasPredicate   
280   ResidentPatient:309          kgc:what   
352              <mask_e>         kgc:where   
111   ResidentPatient:271          kgc:what   
168   ResidentPatient:283    kgc:infoSource   
164   ResidentPatient:282    kgc:infoSource   
75    ResidentPatient:264   kgc:hasProperty   
155   ResidentPatient:280         kgc:where   
114   ResidentPatient:271          kgc:what   
130   ResidentPatient:273          kgc:what   
154   ResidentPatient:280   kgc:hasProperty   
199   ResidentPatient:292       kgc:subject   
171   ResidentPatient:284   kgc:hasProperty   
113   ResidentPatient:271          kgc:what   
303   ResidentPatient:315          kgc:what   
346              <mask_e>    kgc:infoSource   
350              <mask_e>           kgc:why   
150   ResidentPatient:279       kgc:subject   
351              <mask_e>          kgc:what   
185   ResidentPatient:287  kgc:hasPredicate   
106   ResidentPatient:271          kgc:what   
89    ResidentPatient:267          kgc:what   
167   ResidentPatient:283   kgc:hasProperty   
5     ResidentPatient:246   kgc:hasProperty   
342   ResidentPatient:324 

index=344, triple=['ResidentPatient:324', 'kgc:what', 'ResidentPatient:324a'], attention list


...

index=351, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
64    ResidentPatient:262       kgc:subject   
103   ResidentPatient:271       kgc:subject   
240   ResidentPatient:300       kgc:subject   
344   ResidentPatient:324          kgc:what   
44    ResidentPatient:256       kgc:subject   
168   ResidentPatient:283    kgc:infoSource   
48    ResidentPatient:257       kgc:subject   
140   ResidentPatient:276       kgc:subject   
250   ResidentPatient:302       kgc:subject   
245   ResidentPatient:301       kgc:subject   
305   ResidentPatient:316       kgc:subject   
164   ResidentPatient:282    kgc:infoSource   
166   ResidentPatient:283       kgc:subject   
322   ResidentPatient:319          kgc:what   
144   ResidentPatient:277       kgc:subject   
309   ResidentPatient:317       kgc:subject   
152   ResidentPatient:279          kgc:what   
311   ResidentPatient:317       kgc:subject   
124   ResidentPatient:272       kgc:subject   
284   ResidentPatient:310       kgc:subject   
340   ResidentPatient:323          kgc:what   
293   ResidentPatient:312          kgc:what   
73    ResidentPatient:263          kgc:what   
178   ResidentPatient:286       kgc:subject   
336   ResidentPatient:322          kgc:what   
142   ResidentPatient:277       kgc:subject   
170   ResidentPatient:284       kgc:subject   
230   ResidentPatient:298       kgc:subject   
130   ResidentPatient:273          kgc:what   
351              <mask_e>          kgc:what   
316   ResidentPatient:318       kgc:subject   
236   ResidentPatient:299       kgc:subject   
262   ResidentPatient:304       kgc:subject   
157   ResidentPatient:281       kgc:subject   
225   ResidentPatient:297       kgc:subject   
346              <mask_e>    kgc:infoSource   
289   ResidentPatient:311       kgc:subject   
163   ResidentPatient:282          kgc:what   
275   ResidentPatient:308  kgc:hasPredicate   
81    ResidentPatient:266       kgc:subject   
269  ResidentPatient:305a          kgc:what   
319   ResidentPatient:319       kgc:subject   
277   ResidentPatient:308          kgc:when   
314   ResidentPatient:318       kgc:subject   
128   ResidentPatient:273       kgc:subject   
209  ResidentPatient:293a       kgc:subject   
150   ResidentPatient:279       kgc:subject   
160   ResidentPatient:282       kgc:subject   
321   ResidentPatient:319       kgc:subject   
207   ResidentPatient:293          kgc:what   
338   ResidentPatient:323       kgc:subject   
291   ResidentPatient:312       kgc:subject   
13    ResidentPatient:249       kgc:subject   
332   ResidentPatient:321          kgc:when   
145   ResidentPatient:277          kgc:what   
69    ResidentPatient:262          kgc:what   
214   ResidentPatient:294       kgc:subject   
67    ResidentPatient:262          kgc:what   
31    ResidentPatient:253          kgc:time   
11    ResidentPatient:248          kgc:what   
324  ResidentPatient:319a       kgc:subject   
242   ResidentPatient:300  kgc:hasPredicate   
19    ResidentPatient:250          kgc:what   
33    ResidentPatient:254       kgc:subject   
192   ResidentPatient:289          kgc:what   
341               <bos_e>           <bos_r>   
283               <bos_e>           <bos_r>   
201   ResidentPatient:292       kgc:subject   
256   ResidentPatient:303       kgc:subject   
131   ResidentPatient:273          kgc:when   
65    ResidentPatient:262          kgc:what   
17    ResidentPatient:250       kgc:subject   
279   ResidentPatient:309       kgc:subject   
68    ResidentPatient:262          kgc:what   
127   ResidentPatient:273       kgc:subject   
337               <bos_e>           <bos_r>   
317   ResidentPatient:318   kgc:hasProperty   
285   ResidentPatient:310   kgc:hasProperty   
202   ResidentPatient:292          kgc:what   
333               <bos_e>           <bos_r>   
281               <bos_e>           <bos_r>   
26                <bos_e>           <bos_r>   
318               <bos_e>           <bos_r>   
199   ResidentPatient:292       kgc:subject   
330               <bos_e> 

index=352, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
48    ResidentPatient:257       kgc:subject   
64    ResidentPatient:262       kgc:subject   
168   ResidentPatient:283    kgc:infoSource   
164   ResidentPatient:282    kgc:infoSource   
230   ResidentPatient:298       kgc:subject   
11    ResidentPatient:248          kgc:what   
225   ResidentPatient:297       kgc:subject   
332   ResidentPatient:321          kgc:when   
236   ResidentPatient:299       kgc:subject   
103   ResidentPatient:271       kgc:subject   
245   ResidentPatient:301       kgc:subject   
44    ResidentPatient:256       kgc:subject   
277   ResidentPatient:308          kgc:when   
19    ResidentPatient:250          kgc:what   
336   ResidentPatient:322          kgc:what   
240   ResidentPatient:300       kgc:subject   
29    ResidentPatient:253          kgc:when   
226   ResidentPatient:297       kgc:subject   
131   ResidentPatient:273          kgc:when   
161   ResidentPatient:282       kgc:subject   
287   ResidentPatient:310          kgc:when   
30    ResidentPatient:253          kgc:when   
286   ResidentPatient:310          kgc:when   
340   ResidentPatient:323          kgc:what   
253   ResidentPatient:302          kgc:when   
322   ResidentPatient:319          kgc:what   
15    ResidentPatient:249          kgc:what   
142   ResidentPatient:277       kgc:subject   
178   ResidentPatient:286       kgc:subject   
152   ResidentPatient:279          kgc:what   
346              <mask_e>    kgc:infoSource   
241   ResidentPatient:300       kgc:subject   
250   ResidentPatient:302       kgc:subject   
144   ResidentPatient:277       kgc:subject   
81    ResidentPatient:266       kgc:subject   
256   ResidentPatient:303       kgc:subject   
73    ResidentPatient:263          kgc:what   
344   ResidentPatient:324          kgc:what   
160   ResidentPatient:282       kgc:subject   
215   ResidentPatient:294          kgc:what   
77    ResidentPatient:265       kgc:subject   
84    ResidentPatient:266          kgc:when   
182   ResidentPatient:287       kgc:subject   
351              <mask_e>          kgc:what   
130   ResidentPatient:273          kgc:what   
309   ResidentPatient:317       kgc:subject   
145   ResidentPatient:277          kgc:what   
207   ResidentPatient:293          kgc:what   
252   ResidentPatient:302          kgc:what   
143   ResidentPatient:277       kgc:subject   
311   ResidentPatient:317       kgc:subject   
321   ResidentPatient:319       kgc:subject   
316   ResidentPatient:318       kgc:subject   
140   ResidentPatient:276       kgc:subject   
217   ResidentPatient:295       kgc:subject   
319   ResidentPatient:319       kgc:subject   
314   ResidentPatient:318       kgc:subject   
262   ResidentPatient:304       kgc:subject   
170   ResidentPatient:284       kgc:subject   
350              <mask_e>           kgc:why   
238   ResidentPatient:299          kgc:when   
157   ResidentPatient:281       kgc:subject   
17    ResidentPatient:250       kgc:subject   
166   ResidentPatient:283       kgc:subject   
82    ResidentPatient:266       kgc:subject   
13    ResidentPatient:249       kgc:subject   
127   ResidentPatient:273       kgc:subject   
88    ResidentPatient:267       kgc:subject   
192   ResidentPatient:289          kgc:what   
124   ResidentPatient:272       kgc:subject   
25    ResidentPatient:252          kgc:whom   
214   ResidentPatient:294       kgc:subject   
202   ResidentPatient:292          kgc:what   
40    ResidentPatient:255          kgc:when   
41    ResidentPatient:255          kgc:when   
324  ResidentPatient:319a       kgc:subject   
341               <bos_e>           <bos_r>   
85    ResidentPatient:266          kgc:when   
335   ResidentPatient:322   kgc:hasProperty   
9     ResidentPatient:248       kgc:subject   
237   ResidentPatient:299          kgc:when   
80    ResidentPatient:266       kgc:subject   
337               <bos_e>           <bos_r>   
333               <bos_e>           <bos_r>   
173   ResidentPatient:285 

(                              predicate                            whom  \
 ranking                                                                   
 0                   word.predicate:kill     ResidentPatient:Blessington   
 1                   word.predicate:call             DevilsFoot:Roundhay   
 2                     word.predicate:go        SilverBlaze:Silver_Blaze   
 3                word.predicate:examine                 DevilsFoot:Owen   
 4                 word.predicate:return     ResidentPatient:Elderly_man   
 ...                                 ...                             ...   
 7812     DevilsFoot:Four_burning_candle  DevilsFoot:Four_burning_candle   
 7813                    AbbeyGrange:295                 SilverBlaze:253   
 7814                     DevilsFoot:231                  DancingMen:031   
 7815               word.predicate:Break  AbbeyGrange:Findings_of_Holmes   
 7816                    DancingMen:169b              SilverBlaze:Window   
 
          

### 白銀
Who took out the White Silver Blaze? (criminal & explanation) 
被害者: Silver_Blaze
犯人: 
犯行動機:

In [25]:
victim = 'SilverBlaze:Silver_Blaze'
df_ranking_SilverBlaze, df_attension_SilverBlaze = make_ranking(
    'SilverBlaze:330', 'SilverBlaze:396', BRING, MASK_E, MASK_E, MASK_E, victim, MASK_E)

display(df_ranking_SilverBlaze.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SilverBlaze)
for i in range(len_-20, len_):
    display(i, df_attension_SilverBlaze.iloc[i,:3].tolist())
    display(df_attension_SilverBlaze.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

['SilverBlaze:394', 'kgc:hasPredicate', 'word.predicate:buy']

head          relation                        tail  \
53   SilverBlaze:342a           kgc:why  SilverBlaze:white_forehead   
277   SilverBlaze:387           kgc:why            SilverBlaze:387a   
92    SilverBlaze:351  kgc:hasPredicate         word.predicate:kill   
183   SilverBlaze:364           kgc:why             SilverBlaze:365   
196   SilverBlaze:368       kgc:subject   SilverBlaze:horse_trainer   
169   SilverBlaze:360           kgc:why             SilverBlaze:363   
32    SilverBlaze:337  kgc:hasPredicate      word.predicate:notBark   
176   SilverBlaze:362          kgc:what           SilverBlaze:Opium   
150   SilverBlaze:357           kgc:why             SilverBlaze:358   
83            <bos_e>           <bos_r>                     <bos_e>   
190   SilverBlaze:366          kgc:what    SilverBlaze:Lot_of_money   
38            <bos_e>           <bos_r>                     <bos_e>   
319   SilverBlaze:395           kgc:why             SilverBlaze:394   
194   SilverBlaze:367          kgc:what           SilverBlaze:Horse   
26    SilverBlaze:335       kgc:subject         SilverBlaze:3_sheep   
49    SilverBlaze:342           kgc:why            SilverBlaze:342a   
95            <bos_e>           <bos_r>                     <bos_e>   
34            <bos_e>           <bos_r>                     <bos_e>   
86            <bos_e>           <bos_r>                     <bos_e>   
29    SilverBlaze:336  kgc:hasPredicate       word.predicate:wonder   

     atten_from313  
53        0.013412  
277       0.010111  
92        0.009908  
183       0.009458  
196       0.008649  
169       0.008152  
32        0.007824  
176       0.007543  
150       0.007422  
83        0.007197  
190       0.007066  
38        0.006874  
319       0.006794  
194       0.006602  
26        0.006602  
49        0.006573  
95        0.006525  
34        0.006269  
86        0.006054  
29        0.005957

----------


314

['SilverBlaze:394', 'kgc:what', 'SilverBlaze:Expensive_clothes']

...

----------


332

['<mask_e>', 'kgc:where', '<mask_e>']

head     relation                               tail  \
80    SilverBlaze:348  kgc:subject                    AllTitle:Holmes   
4     SilverBlaze:331  kgc:subject                    AllTitle:Holmes   
87    SilverBlaze:349  kgc:subject                    AllTitle:Holmes   
227   SilverBlaze:375     kgc:when                    SilverBlaze:371   
76    SilverBlaze:347  kgc:subject                    AllTitle:Holmes   
308  SilverBlaze:393a  kgc:subject                    AllTitle:Holmes   
277   SilverBlaze:387      kgc:why                   SilverBlaze:387a   
53   SilverBlaze:342a      kgc:why         SilverBlaze:white_forehead   
16    SilverBlaze:333  kgc:subject                    AllTitle:Holmes   
64    SilverBlaze:345  kgc:subject                    AllTitle:Holmes   
250   SilverBlaze:382     kgc:when  SilverBlaze:Night_of_the_incident   
186   SilverBlaze:365     kgc:when  SilverBlaze:Night_of_the_incident   
210  SilverBlaze:371a     kgc:what           SilverBlaze:Silver_Blaze   
257   SilverBlaze:383     kgc:when                   SilverBlaze:383a   
190   SilverBlaze:366     kgc:what           SilverBlaze:Lot_of_money   
223   SilverBlaze:374      kgc:why                    SilverBlaze:375   
285   SilverBlaze:388     kgc:when                    SilverBlaze:387   
164   SilverBlaze:360  kgc:subject                    AllTitle:Holmes   
298   SilverBlaze:391     kgc:when                    SilverBlaze:385   
275   SilverBlaze:387  kgc:subject           SilverBlaze:Silver_Blaze   

     atten_from332  
80        0.025011  
4         0.021244  
87        0.019538  
227       0.014160  
76        0.013804  
308       0.013054  
277       0.012800  
53        0.012208  
16        0.011694  
64        0.011122  
250       0.011066  
186       0.010831  
210       0.010722  
257       0.009239  
190       0.009138  
223       0.009097  
285       0.009046  
164       0.008840  
298       0.008742  
275       0.008505

----------


### CrookedMan(背中の曲がった男):
Why did Barclay die?
被害者: Barclay
犯人:
犯行動機:

In [26]:
victim = 'CrookedMan:Barclay'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    f'CrookedMan:{373-80+1}', 'CrookedMan:373', DIE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_CrookedMan)
for i in range(len_-20, len_):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                               whom  \
0                     word.predicate:die                   CrookedMan:Nancy   
1                    word.predicate:have                 CrookedMan:Barclay   
2      SilverBlaze:Night_of_the_incident                            <bos_e>   
3                    word.predicate:fire                DevilsFoot:Roundhay   
4           DateTime:1883-04-01T10:00:00           SilverBlaze:John_Straker   
5                   word.predicate:marry                   CrookedMan:Henry   
6          SilverBlaze:Gregory_Inspector                 word.predicate:say   
7                                <bos_e>  SilverBlaze:Night_of_the_incident   
8   AbbeyGrange:Sir_Eustace_Brackenstall                    AllTitle:Holmes   
9           SpeckledBand:Julia_s_bedroom              CrookedMan:1857-07-09   
10                  word.predicate:enter      SilverBlaze:Inspector_Gregory   
11            word.predicate:beSurprised        DancingMen:1898-08-13T03:00   
12                      CrookedMan:Nancy        SilverBlaze:Horseshoe_marks   
13                word.predicate:collect                DevilsFoot:Mortimer   
14          DateTime:1857-07-09T00:00:00                word.predicate:wear   
15                   word.predicate:meet     CrookedMan:1887-07-06T21:15:00   
16             ResidentPatient:Young_man    ResidentPatient:Percy_Trevelyan   
17                     word.predicate:go             word.predicate:request   
18                  word.predicate:shoot               word.predicate:think   
19                SilverBlaze:Ned_Hunter                  DevilsFoot:Porter   

                              subject                                     why  \
0                  CrookedMan:Barclay                                 <bos_e>   
1                    CrookedMan:Nancy                        CrookedMan:Nancy   
2                             <bos_e>                     DevilsFoot:Roundhay   
3            SilverBlaze:John_Straker                       word.predicate:go   
4                     AllTitle:Holmes            SpeckledBand:Julia_s_bedroom   
5                    CrookedMan:Henry                     word.predicate:wear   
6                     AllTitle:Watson                         AllTitle:Watson   
7      CrookedMan:1887-07-06T21:15:00                      SpeckledBand:Helen   
8                  word.predicate:say                         AllTitle:Holmes   
9         SilverBlaze:Horseshoe_marks                SilverBlaze:John_Straker   
10         SpeckledBand:1883-04-01T10                     word.predicate:know   
11      SilverBlaze:Gregory_Inspector                      CrookedMan:Barclay   
12          ResidentPatient:Young_man                    word.predicate:upset   
13              CrookedMan:1857-07-09                  word.predicate:notKnow   
14  SilverBlaze:Night_of_the_incident  AbbeyGrange:Thought_of_Stanley_Hopkins   
15               word.predicate:think                 word.predicate:notExist   
16               word.predicate:exist             DancingMen:1898-08-13T03:00   
17                DevilsFoot:Roundhay              SpeckledBand:1883-04-01T07   
18    ResidentPatient:Percy_Trevelyan                    word.predicate:drawn   
19               word.predicate:goOut               SilverBlaze:two_young_men   

                            what                          where  
0                        <bos_e>                        <bos_e>  
1               CrookedMan:Nancy               CrookedMan:Nancy  
2              word.predicate:go            DevilsFoot:Roundhay  
3       SilverBlaze:John_Straker       SilverBlaze:John_Straker  
4             CrookedMan:Barclay           word.predicate:think  
5            DevilsFoot:Roundhay              word.predicate:go  
6     SpeckledBand:1883-04-01T15                AllTitle:Holmes  
7             SpeckledBand:Helen             CrookedMan:Barclay  
8                AllTitle:Holmes         word.predicate:notHave  
9        

334

['CrookedMan:371', 'kgc:subject', 'CrookedMan:Barclay']

head         relation                          tail  \
210   CrookedMan:339         kgc:what              CrookedMan:beast   
321   CrookedMan:368         kgc:what                CrookedMan:369   
324   CrookedMan:368         kgc:what                CrookedMan:372   
322   CrookedMan:368         kgc:what                CrookedMan:370   
222   CrookedMan:343         kgc:what     CrookedMan:foot_of_ermine   
278   CrookedMan:359         kgc:what                CrookedMan:360   
323   CrookedMan:368         kgc:what                CrookedMan:371   
256  CrookedMan:352a  kgc:hasProperty          word.predicate:snake   
232   CrookedMan:346         kgc:what                CrookedMan:347   
285   CrookedMan:361          kgc:why                CrookedMan:359   
122  CrookedMan:318a         kgc:what                CrookedMan:086   
253   CrookedMan:352         kgc:what              CrookedMan:cobra   
344   CrookedMan:373         kgc:what  CrookedMan:preface_of_Samuel   
327   CrookedMan:369  kgc:hasProperty          word.predicate:David   
220   CrookedMan:342  kgc:hasProperty         word.predicate:supple   
228   CrookedMan:345  kgc:hasProperty            word.predicate:red   
260   CrookedMan:353         kgc:what              CrookedMan:cobra   
294   CrookedMan:363          kgc:why               CrookedMan:363a   
217   CrookedMan:341  kgc:hasProperty           word.predicate:thin   
227   CrookedMan:345      kgc:subject       CrookedMan:eye_of_beast   

     atten_from334  
210       0.014078  
321       0.011559  
324       0.011149  
322       0.011106  
222       0.010833  
278       0.010756  
323       0.010606  
256       0.010432  
232       0.009972  
285       0.009375  
122       0.009136  
253       0.008440  
344       0.007758  
327       0.007199  
220       0.007033  
228       0.006942  
260       0.006369  
294       0.006355  
217       0.006313  
227       0.006256

----------


...

----------


353

['<mask_e>', 'kgc:where', '<mask_e>']

head         relation  \
205   CrookedMan:338      kgc:subject   
255  CrookedMan:352a      kgc:subject   
249   CrookedMan:351  kgc:hasProperty   
230   CrookedMan:346      kgc:subject   
282   CrookedMan:360         kgc:when   
151   CrookedMan:326   kgc:infoSource   
256  CrookedMan:352a  kgc:hasProperty   
296  CrookedMan:363a      kgc:subject   
53    CrookedMan:306   kgc:infoSource   
253   CrookedMan:352         kgc:what   
323   CrookedMan:368         kgc:what   
324   CrookedMan:368         kgc:what   
322   CrookedMan:368         kgc:what   
261   CrookedMan:353         kgc:when   
30    CrookedMan:301   kgc:infoSource   
327   CrookedMan:369  kgc:hasProperty   
284   CrookedMan:361      kgc:subject   
228   CrookedMan:345  kgc:hasProperty   
258   CrookedMan:353      kgc:subject   
321   CrookedMan:368         kgc:what   

                                          tail  atten_from353  
205                            AllTitle:Holmes       0.028347  
255                           CrookedMan:cobra       0.020368  
249                       word.predicate:Teddy       0.019520  
230                            AllTitle:Holmes       0.018094  
282                        CrookedMan:30_years       0.017924  
151                           CrookedMan:Henry       0.017549  
256                       word.predicate:snake       0.016803  
296                            AllTitle:Holmes       0.015028  
53                            CrookedMan:Henry       0.015009  
253                           CrookedMan:cobra       0.014803  
323                             CrookedMan:371       0.012141  
324                             CrookedMan:372       0.011944  
322                             CrookedMan:370       0.011800  
261                     CrookedMan:every_night       0.011558  
30   CrookedMan:Nancy_AND_old_friends_of_Henry       0.011079  
327                       word.predicate:David       0.010854  
284                           CrookedMan:Henry       0.010454  
228                         word.predicate:red       0.009864  
258                           CrookedMan:Teddy       0.009700  
321                             CrookedMan:369       0.009296

----------


### 花嫁失踪事件（同一事件）
hozmaの失踪の名瀬を探る
被害者: ACaseOfIdentity:Hozma
犯人: 
犯行動機: 

In [27]:
victim = 'ACaseOfIdentity:Hosmer'
df_ranking_ACaseOfIdentity, df_attension_ACaseOfIdentity = make_ranking(
    'ACaseOfIdentity:510', 'ACaseOfIdentity:578', HIDE, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_ACaseOfIdentity.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_ACaseOfIdentity)
for i in range(len_-20, len_):
    display(i, df_attension_ACaseOfIdentity.iloc[i,:3].tolist())
    display(df_attension_ACaseOfIdentity.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")


predicate                               whom  \
0                          AllTitle:Holmes             ACaseOfIdentity:Hosmer   
1               ACaseOfIdentity:Sutherland                            <bos_e>   
2                      DevilsFoot:Mortimer                    AllTitle:Holmes   
3                     word.predicate:think                  DevilsFoot:window   
4                    word.predicate:arrive         ACaseOfIdentity:Sutherland   
5                     word.predicate:exist                    AllTitle:Watson   
6                         CrookedMan:Henry                DevilsFoot:Roundhay   
7                   word.predicate:suicide                  DevilsFoot:Brenda   
8                ResidentPatient:Young_man      SilverBlaze:Inspector_Gregory   
9                      word.predicate:call                word.predicate:find   
10  AbbeyGrange:Thought_of_Stanley_Hopkins                   CrookedMan:Henry   
11                    word.predicate:close        ResidentPatient:Blessington   
12                     word.predicate:hear        SilverBlaze:Horseshoe_marks   
13                      word.predicate:see               word.predicate:think   
14                     word.predicate:wear                word.predicate:meet   
15                        CrookedMan:beast                word.predicate:wear   
16                    word.predicate:shoot             word.predicate:notHave   
17             ResidentPatient:Blessington                 CrookedMan:Barclay   
18         SpeckledBand:mansion_of_Roylott           SilverBlaze:John_Straker   
19                   word.predicate:escape  SilverBlaze:Night_of_the_incident   

                                 subject                         why  \
0              ACaseOfIdentity:Windibank                     <bos_e>   
1                                <bos_e>            CrookedMan:Nancy   
2                        AllTitle:Holmes    SilverBlaze:John_Straker   
3        ResidentPatient:Percy_Trevelyan         DevilsFoot:Roundhay   
4            DancingMen:1898-08-13T11:00         word.predicate:wear   
5              SilverBlaze:two_young_men         word.predicate:find   
6            ResidentPatient:Blessington         word.predicate:know   
7           DateTime:1883-04-01T23:00:00             AllTitle:Holmes   
8                    word.predicate:wear           word.predicate:go   
9                 CrookedMan:living_room         word.predicate:hear   
10                    CrookedMan:Barclay  SpeckledBand:1883-04-01T15   
11          DateTime:1883-04-01T14:00:00             AllTitle:Watson   
12                    word.predicate:try   SilverBlaze:two_young_men   
13  AbbeyGrange:Sir_Eustace_Brackenstall          SpeckledBand:Helen   
14                   word.predicate:know      SilverBlaze:Ned_Hunter   
15                   word.predicate:hear      word.predicate:notKnow   
16                     word.predicate:go        word.predicate:think   
17                      CrookedMan:Nancy    SilverBlaze:Colonel_Ross   
18                   DevilsFoot:Roundhay     AbbeyGrange:Jack_Croker   
19           SilverBlaze:Fitzroy_Simpson         word.predicate:want   

                                 what                             where  
0                             <bos_e>                           <bos_e>  
1                 word.predicate:find                   AllTitle:Holmes  
2                 word.predicate:know          SilverBlaze:John_Straker  
3            SilverBlaze:John_Straker               word.predicate:find  
4                   word.predicate:go         SilverBlaze:two_young_men  
5                  SpeckledBand:Helen            SilverBlaze:Ned_Hunter  
6                    CrookedMan:Nancy                 word.predicate:go  
7                 word.predicate:wear       DancingMen:1898-08-13T11:00  
8              SilverBlaze:Ned_Hunter               word.predicate:wear  
9                     AllTitle:Holmes   SpeckledBand:mansion_of_Roylott  
10  

293

['ACaseOfIdentity:576', 'kgc:subject', 'ACaseOfIdentity:company']

head        relation  \
189  ACaseOfIdentity:555        kgc:what   
244  ACaseOfIdentity:564        kgc:what   
299  ACaseOfIdentity:577        kgc:what   
245  ACaseOfIdentity:564        kgc:what   
282  ACaseOfIdentity:573  kgc:infoSource   
261  ACaseOfIdentity:569  kgc:infoSource   
1    ACaseOfIdentity:510     kgc:subject   
260  ACaseOfIdentity:569        kgc:what   
259  ACaseOfIdentity:569     kgc:subject   
30   ACaseOfIdentity:511  kgc:infoSource   
291  ACaseOfIdentity:575  kgc:infoSource   
9    ACaseOfIdentity:510        kgc:what   
50   ACaseOfIdentity:516  kgc:infoSource   
209  ACaseOfIdentity:558        kgc:what   
20   ACaseOfIdentity:510        kgc:what   
278  ACaseOfIdentity:572  kgc:infoSource   
218  ACaseOfIdentity:558        kgc:what   
214  ACaseOfIdentity:558        kgc:what   
219  ACaseOfIdentity:558        kgc:what   
47   ACaseOfIdentity:515  kgc:infoSource   

                                     tail  atten_from293  
189                  ACaseOfIdentity:555a       0.009406  
244         ACaseOfIdentity:Color_glasses       0.009387  
299             ACaseOfIdentity:Windibank       0.008460  
245              ACaseOfIdentity:disguise       0.007751  
282                       AllTitle:Holmes       0.007611  
261                       AllTitle:Holmes       0.007577  
1                         AllTitle:Holmes       0.007091  
260  ACaseOfIdentity:company_of_Windibank       0.006540  
259                       AllTitle:Holmes       0.006505  
30                        AllTitle:Holmes       0.006390  
291                       AllTitle:Holmes       0.006343  
9                     ACaseOfIdentity:522       0.006295  
50                        AllTitle:Holmes       0.006228  
209                   ACaseOfIdentity:565       0.006213  
20                    ACaseOfIdentity:533       0.006157  
278                       AllTitle:Holmes       0.005998  
218                   ACaseOfIdentity:576       0.005969  
214                   ACaseOfIdentity:572       0.005959  
219                   ACaseOfIdentity:578       0.005821  
47                        AllTitle:Holmes       0.005804

----------


...

----------


312

['<mask_e>', 'kgc:where', '<mask_e>']

head        relation  \
112   ACaseOfIdentity:534     kgc:subject   
302   ACaseOfIdentity:578     kgc:subject   
168   ACaseOfIdentity:550     kgc:subject   
111   ACaseOfIdentity:534     kgc:subject   
32    ACaseOfIdentity:512     kgc:subject   
157   ACaseOfIdentity:547     kgc:subject   
162   ACaseOfIdentity:548     kgc:subject   
80    ACaseOfIdentity:525     kgc:subject   
116   ACaseOfIdentity:535     kgc:subject   
236   ACaseOfIdentity:562  kgc:infoSource   
180   ACaseOfIdentity:553     kgc:subject   
179   ACaseOfIdentity:553     kgc:subject   
183   ACaseOfIdentity:553  kgc:infoSource   
87   ACaseOfIdentity:527a     kgc:subject   
282   ACaseOfIdentity:573  kgc:infoSource   
286   ACaseOfIdentity:574  kgc:infoSource   
297   ACaseOfIdentity:577     kgc:subject   
50    ACaseOfIdentity:516  kgc:infoSource   
47    ACaseOfIdentity:515  kgc:infoSource   
254   ACaseOfIdentity:566  kgc:infoSource   

                                      tail  atten_from312  
112        ACaseOfIdentity:death_of_Hosmer       0.021158  
302             ACaseOfIdentity:Sutherland       0.018123  
168                        AllTitle:Holmes       0.016392  
111         ACaseOfIdentity:Life_of_Hosmer       0.015925  
32              ACaseOfIdentity:Sutherland       0.012655  
157                        AllTitle:Holmes       0.012644  
162                        AllTitle:Holmes       0.012337  
80              ACaseOfIdentity:Sutherland       0.011653  
116              ACaseOfIdentity:Windibank       0.011503  
236                        AllTitle:Holmes       0.011261  
180   ACaseOfIdentity:friend_of_Sutherland       0.011137  
179  ACaseOfIdentity:brother_of_Sutherland       0.010442  
183                        AllTitle:Holmes       0.010410  
87              ACaseOfIdentity:Sutherland       0.010096  
282                        AllTitle:Holmes       0.009848  
286                        AllTitle:Holmes       0.009614  
297     ACaseOfIdentity:Personal_statement       0.009338  
50                         AllTitle:Holmes       0.009247  
47                         AllTitle:Holmes       0.009177  
254                        AllTitle:Holmes       0.008893

----------
